# Amine Djeghri

## Préparation

Environnement d'exécution des requêtes

In [0]:
# on utilise 8 partitions au lieu de 200 par défaut
spark.conf.set("spark.sql.shuffle.partitions", "8")
print("Nombre de partitions utilisées : ", spark.conf.get("spark.sql.shuffle.partitions"))

Nombre de partitions utilisées : 8

URL pour accès aux datasets

In [0]:
# URL du dossier PUBLIC_DATASET contenant des fichiers de données pour les TP
# ---------------------------------------------------------------------------
# en cas de problème avec le téléchargement des datasets, aller directement sur l'URL ci-dessous
PUBLIC_DATASET_URL = "https://nuage.lip6.fr/s/H3bpyRGgnCq2NR4" 
PUBLIC_DATASET=PUBLIC_DATASET_URL + "/download?path="

print("URL pour les datasets ", PUBLIC_DATASET_URL)

URL pour les datasets https://nuage.lip6.fr/s/H3bpyRGgnCq2NR4

### Uploader les datasets de IMDB

Cette étape est à faire une seule fois afin de sauvegarder les données du TP dans votre espace de stockage Databricks.
Télécharger l'archive contenant les fichiers IMDB.
Dans PUBLIC_DATASET https://nuage.lip6.fr/s/H3bpyRGgnCq2NR4
aller dans le dossier imdb/vldb2015 et télécharger le fichier csvfiles_sample001.tgz

Lien direct :
https://nuage.lip6.fr/s/H3bpyRGgnCq2NR4/download?path=/imdb/vldb2015&files=csvfiles_sample001.tgz

Extraire les fichiers csv de l'archive

Menu Data -> Add Data
Sélectionner un nouveau dossier pour _DBFS target directory_  /FileStore/tables/**imdb**
puis uploader tous les fichiers csv dans ce directory.

Liste des fichiers IMDB :

In [0]:
print("imdb")
display(dbutils.fs.ls("dbfs:/FileStore/tables/imdb"))

path name size dbfs:/FileStore/tables/imdb/cast_info.csv cast_info.csv 15368545 dbfs:/FileStore/tables/imdb/company_name.csv company_name.csv 894637 dbfs:/FileStore/tables/imdb/company_type.csv company_type.csv 92 dbfs:/FileStore/tables/imdb/info_type.csv info_type.csv 1928 dbfs:/FileStore/tables/imdb/kind_type.csv kind_type.csv 85 dbfs:/FileStore/tables/imdb/movie_companies.csv movie_companies.csv 956556 dbfs:/FileStore/tables/imdb/movie_info.csv movie_info.csv 9854170 dbfs:/FileStore/tables/imdb/name.csv name.csv 17549614 dbfs:/FileStore/tables/imdb/person_info.csv person_info.csv 145007548 dbfs:/FileStore/tables/imdb/role_type.csv role_type.csv 160 dbfs:/FileStore/tables/imdb/title.csv title.csv 2262112

## Définir les tables de la base IMDB

Le dossier contenant les fichiers csv de IMDB

In [0]:
dir = "/FileStore/tables/imdb/"

La table Title affecte un identifiant id à un film

In [0]:
schema_title = """
          id INT, 
          title STRING, 
          imdb_index STRING, 
          kind_id INT, 
          production_year INT, 
          imdb_id INT, 
          phonetic_code STRING, 
          episode_id STRING,
          season_nr INT, 
          episode_nr INT, 
          series_years STRING, 
          md5sum STRING
        """

title = spark.read.csv(path = dir + "title.csv", schema = schema_title).persist()
title.createOrReplaceTempView("Title")
display(title)

id title imdb_index kind_id production_year imdb_id phonetic_code episode_id season_nr episode_nr series_years md5sum 7532 Beautiful, Married & Missing null 7 2009 null B3145 7383 null null null 890adf0e8ff5ba69b8f6dc7b0dce84e7 160794 Self-Awareness as a Soldier! Strength Lies in the Pure Heart null 7 1995 null S4165 160772 1 38 null eb32612a744424c3b79a8959c48aa89b 20232 Baby Manning null 7 1998 null B152 20037 null null null 825389d4e35f378f950238020942782e 16604 The Next First Lady?/Here Comes the Girls/Toni Morrison null 7 1999 null N2316 15711 31 20 null 6385686401009aa7277c38cea7db489c 189974 (#1.6) null 7 2000 null null 189966 1 6 null 2b97f31e49e4cea3da14e1d1292915d2 7034 (2001-04-26) null 7 2001 null null 6845 null null null b5773a56b3c21479ceada92cb3840612 63988 (2010-04-09) null 7 2010 null null 63983 null null null 0f95b8ecd807c9e10b5181ffab8b6bf7 128719 (1999-03-03) null 7 1999 null null 128714 null null null 0b40df9322c04d540aa496bf719eb265 12434 New Best Friend null 7 2013 null N1231 12433 1 3 null 9002eef5ad46236af79c0c7be159668b 109725 (2010-01-04) null 7 2010 null null 109693 null null null a3ee822c5e48f29313f30f674c5e9e13 139353 (2006-05-15) null 7 2006 null null 139148 null null null b74f07145ced11b66893049aefe839a9 178658 (2001-09-06) null 7 2001 null null 178599 null null null 1377141468ad57bf6617a26efc759e39 21960 Will to Win: Part 2 null 7 1986 null W4351 20918 6 14 null 85e3ac3d42b8df56f44699d297277e56 16988 Das Jahr 2006 null 7 2009 null J6 16930 1 58 null facfd517532601ff0564cbba0e4aa5fa 196977 Paradise null 7 null null P632 196812 null null null 4c25d10ec2962e422bb6b3d5a8c71cfd 12758 DNA null 7 2010 null D5 12751 1 13 null e38f0b8cdd96264c5c8bf2b6c174adba 75956 Nog een appeltje? null 7 2010 null N2514 75834 3 23 null 88e946c7e0cd816e9da8b83ea50892f4 180939 The Real MacGyver null 7 2013 null R4521 180927 2 2 null 7ef6efa65bdd983f13cae9ff14ac4cf7 31819 Aa Megami ni kokoro ubawarete? null 7 2005 null A5252 31807 1 15 null cd3d7416b01fabb7f206d12524929800 13473 The Stranger You Know null 7 2013 null S3652 13245 null null null 4ae782b8f9a4907cc17c6f055c043f7f 93064 (1979-08-18) null 7 1979 null null 93031 null null null c3644b3cbe52ac94b4394538cd4c552f 120285 Baar null 2 2004 null B6 null null null 2004-???? 77d222e1822fa1d6bac726295fa0cac8 125325 All Bar One null 7 1998 null A4165 125323 4 1 null 2491b5daf6302b4fd85ea1b068b4a99a 74615 Martin Scorsese Directs null 7 1990 null M6352 74512 5 3 null 72bdaa16e9a4e817de535c2c5db99a25 15064 (#4.35) null 7 2011 null null 14924 4 35 null f1957aa7714119d6d0ab7ee123532c4b 99302 Tunnel to Freedom null 7 1962 null T5431 98906 13 4 null 3d45a5ad77e96416ad6978c3d73c22e2 164413 (#2.19) null 7 null null null 164254 2 19 null 14b9d285aa052027e4f963aed562593f 59741 Let's Spend the Night Together null 7 1992 null L3215 59693 3 23 null 4c7bdfddf0265d25da169936bc746a93 119726 (#7.26) null 7 2012 null null 119552 7 26 null 85815cfd0cb421cfd87d6d7a9a25d28f 134136 (2008-07-15) null 7 2008 null null 134128 null null null f0d75e995c17b00f8d70a7718682019b 130237 We've Got Rhythm! null 7 1997 null W1236 129983 4 4 null d70025d15e8786250655a5d293030f4b 39926 Motivational Chat with Kyra Batte and John Michael Ferrari null 7 2012 null M3135 39009 4 216 null 773e745aabd0f13c140c28ab26a23893 81051 Star-Crossed null 7 2001 null S3626 80989 1 20 null 4595bd858fb75d531b30d5456ca1154c 3138 (#2.55) null 7 2008 null null 3083 2 55 null ca76df3bf275d586b8935d0c4ee32d89 73528 Best Laid Plans null 7 2012 null B2343 73525 2 5 null e272cbbaced1638ee842acfd6b55dca9 163320 A Bridge Too Weak null 7 null null B6323 163319 1 2 null 59a787ce50781857cd5b06f6f28a5e0b 145652 De moord van Liedekerke null 7 1966 null M6315 145651 null null null 2b4be51c9023d5b0b8f577929b359cf6 66850 Quintero amenaza a Camilo null 7 2008 null Q5365 65509 null null null 07951b0449fb921d0efc43e429e6026c 186574 To Everything a Season null 7 1988 null T1635 186555 1 17 null 6481702c1edfe67ac3dba9afada01197 152456 (#2.40) null 7 2

La table Kind_type

In [0]:
#============
# Kind_Type
#============
schema_kind_type = "id INT, kind STRING"

kind_type = spark.read.csv(path = dir + "kind_type.csv", schema = schema_kind_type).persist()

kind_type.createOrReplaceTempView("Kind_Type")
#kind_type.printSchema()
display(kind_type)

id kind 1 movie 2 tv series 3 tv movie 4 video movie 5 tv mini series 6 video game 7 episode

La table Info_type indique la nature d'un attribut d'information. 
Sert dans Movie_Info, Person_Info

In [0]:
#==============
# Info_Type
#==============
schema_info_type = "id INT, info STRING"

info_type = spark.read.csv(path = dir + "info_type.csv", schema = schema_info_type).persist()

info_type.createOrReplaceTempView("Info_Type")
#info_type.printSchema()

display(info_type)

id info 1 runtimes 2 color info 3 genres 4 languages 5 certificates 6 sound mix 7 tech info 8 countries 9 taglines 10 keywords 11 alternate versions 12 crazy credits 13 goofs 14 soundtrack 15 quotes 16 release dates 17 trivia 18 locations 19 mini biography 20 birth notes 21 birth date 22 height 23 death date 24 spouse 25 other works 26 birth name 27 salary history 28 nick names 29 books 30 agent address 31 biographical movies 32 portrayed in 33 where now 34 trade mark 35 interviews 36 article 37 magazine cover photo 38 pictorial 39 death notes 40 LD disc format 41 LD year 42 LD digital sound 43 LD official retail price 44 LD frequency response 45 LD pressing plant 46 LD length 47 LD language 48 LD review 49 LD spaciality 50 LD release date 51 LD production country 52 LD contrast 53 LD color rendition 54 LD picture format 55 LD video noise 56 LD video artifacts 57 LD release country 58 LD sharpness 59 LD dynamic range 60 LD audio noise 61 LD color information 62 LD group genre 63 LD quality program 64 LD close captions-teletext-ld-g 65 LD category 66 LD analog left 67 LD certification 68 LD audio quality 69 LD video quality 70 LD aspect ratio 71 LD analog right 72 LD additional information 73 LD number of chapter stops 74 LD dialogue intellegibility 75 LD disc size 76 LD master format 77 LD subtitles 78 LD status of availablility 79 LD quality of source 80 LD number of sides 81 LD video standard 82 LD supplement 83 LD original title 84 LD sound encoding 85 LD number 86 LD label 87 LD catalog number 88 LD laserdisc title 89 screenplay-teleplay 90 novel 91 adaption 92 book 93 production process protocol 94 printed media reviews 95 essays 96 other literature 97 mpaa 98 plot 99 votes distribution 100 votes 101 rating 102 production dates 103 copyright holder 104 filming dates 105 budget 106 weekend gross 107 gross 108 opening weekend 109 rentals 110 admissions 111 studios 112 top 250 rank 113 bottom 10 rank

La table Movie_info

In [0]:
#==============
# Movie_Info
#==============
schema_movie_info = """
    id int,
    movie_id int,
    info_type_id int,
    info string,
    note string
"""

movie_info = spark.read.csv(path = dir + "movie_info.csv", schema = schema_movie_info).persist()

movie_info.createOrReplaceTempView("Movie_Info")
#movie_info.printSchema()

display(movie_info)

id movie_id info_type_id info note 11658949 13 16 Italy:29 March 2012 null 11659887 434 16 Netherlands:7 January 2013 null 11661227 1680 16 USA:11 May 2011 null 11661228 1680 16 USA:11 May 2011 null 11661771 1841 16 Spain:20 March 2005 null 11662532 2907 16 Spain:28 September 2002 null 11662603 2977 16 USA:22 August 2011 null 11663044 3228 16 USA:27 September 1997 null 214865 3228 15 Two-Tone: [watches Nanny set a yard sale box down] Yard sales! I love yard sales! Actually I hate yard sales, the pros of a yard sale are the great bargains but the cons of a yard sale are that everything is used, eww yuck::Cadpig: Two-Tone... FOCUS! null 214866 3228 15 Rolly: Anybody want a peanut?... What? It's not like I've offered you some of my food before. Okay, so it's been a while. null 214867 3228 15 Cadpig: Uh-oh! I'm having an out-of-bubble experience! null 214868 3228 15 Two-Tone: Hi, Mooch. Beautiful morning, isn't it?::Mooch: It was. I can't see it anymore! null 214869 3228 15 Two-Tone: Oh, Mooch? I just came by to say to you, I have nothing to say to you. If I had anything to say to you, I'd say it to Lucky, my date tonight at the dance.::Mooch: Say what? You always go out with me!::Two-Tone: Correction. Used to go with you, but you didn't ask me; Lucky did. null 214870 3228 15 Two-Tone: Don't hide, Lucky. I like your new look.::Lucky: No, you don't. Mooch is right. You don't want to be seen with me.::Two-Tone: Yes, I do! You're still Lucky. I think you're cool in any color.::Lucky: Really?::Two-Tone: Yeah. null 214871 3228 15 Rolly: Hey, watch where you're going, you clumsy box! null 214872 3228 15 Cadpig: No glitz, no glory. null 214873 3228 15 Lucky: The farm looks fantastic! Just looking at it makes me feel so... itchy!::Cadpig: What are you so itchy about?::Lucky: I'm itching to go to the dance with Two-Tone.::Cadpig: Someone's been bitten by the puppy love bug.::Lucky: Well, that explains why I itch... but does it explain why I hear music? null 214874 3228 15 Two-Tone: [to Mooch] I just came by here to say to you that I have nothing to say to you. If I had anything to say to you, I'd say it to Lucky... my date tonight at the dance! null 214875 3228 15 Two-Tone: Yard sales? I love yard sales! Actually, I hate yard sales. The pros of a yard sale are the bargains, but the cons of a yard sale are that the items are used! Ugh!::Cadpig: Two-Tone? Focus! null 214876 3228 15 Lucky: Where did you learn about this?::Spot: I'm Professor Egghead Science Over-Easy! null 214877 3228 15 Two-Tone: Hi, Mooch. Beautiful morning, isn't it?::Mooch: It was! I can't see it anymore! null 214878 3228 15 Lucky: I look like a big wad of bubble gum.::Rolly: Then why'd you dye yourself pink? You shoulda picked another color! null 214879 3228 15 Spot: How do you hide an elephant?::Rolly: Maybe we can put him on wheels and disguise him as a vacuum cleaner.::Spot: Or stick little magnets on him and pretend he's a refrigerator.::Cadpig: Or put a saddle on his back and pretend he's a horse with a glandular problem. null 214880 3228 15 Rolly: Anybody want some peanuts?::[the other pups give strange looks]::Rolly: What? It's not like I've never offered you any of my food before. Okay, so it's been a while. null 214881 3228 15 Cadpig: Uh-oh! I'm having and out-of-bubble experience! null 2873294 3342 2 Color null 8980758 3342 1 90 null 4162195 3342 8 USA null 11663164 3342 16 USA:September 2000 null 5486968 3342 3 Music null 14695682 3342 9 You pick 'em. We play 'em. null 7021604 3342 4 English null 11663167 3345 16 USA:23 August 2001 null 11663315 3493 16 USA:18 August 2006 null 11663365 3544 16 USA:17 September 2004 null 2873429 3981 2 Color null 8320156 3981 18 Action Concept Studios, Hürth-Kalscheuren, North Rhine - Westphalia, Germany (studio) 4162328 3981 8 Germany null 8320157 3981 18 Hürth, North Rhine - Westphalia, Germany (studio) 7021739 3981 4 German null 8320158 3981 18 North Rhine - Westphalia, Germany null 11663905 3981 16 Germany:22 October 2008 n

La table Cast_Info

In [0]:
#==============
# Cast_Info
#==============
schema_cast_info = """
  id int,
  person_id int,
  movie_id int,
  person_role_id int,
  note string,
  nr_order int,
  role_id int
"""

cast_info = spark.read.csv(path = dir + "cast_info.csv", schema = schema_cast_info).persist()

cast_info.createOrReplaceTempView("Cast_Info")
#cast_info.printSchema()

display(cast_info)

id person_id movie_id person_role_id note nr_order role_id 16255404 2202581 434 2671901 null 9 2 31519800 3558778 434 null null null 9 16668206 2256708 434 2264435 null 2 2 1148671 159670 434 271127 null 1 1 18308464 2464312 434 2922782 null null 2 3164925 423423 434 9407 null null 1 19291922 2593019 434 3040044 null 4 2 5264485 705755 434 1013996 null 3 1 19618701 2634949 434 2182050 null 5 2 5806077 786248 434 1107705 null 6 1 27721477 3312885 434 null null null 5 10861176 1487801 434 955345 null 8 1 12920066 1770691 434 2194685 null 7 2 33055709 3714443 1680 null (production assistant) null 10 2912973 387262 1680 53 null null 1 21230535 2801406 1680 null (post producer) null 3 21524423 2826019 1680 null (supervising producer) null 3 22622086 1084034 1680 null (executive producer) null 3 22800281 2943775 1680 null (producer) null 3 22918278 2955833 1680 null (producer) null 3 30278049 3304029 1680 null null null 8 7730160 1053812 1841 1 null null 1 18271798 2460407 2907 270846 null null 2 18697034 2514889 2977 18504 (Angry Wife) null 2 31078208 3530014 2977 null null null 9 19890569 2668534 2977 15800 null null 2 31134990 987079 2977 null null null 9 20370348 115891 2977 null (executive producer) null 3 31261248 1190579 2977 null null null 9 20641979 229095 2977 null (story producer) null 3 31468925 1519016 2977 null null null 9 22474291 2913596 2977 null (executive producer) null 3 31689471 3230279 2977 null (production assistant) null 10 22826175 2946333 2977 null (associate producer) null 3 33645900 2868803 2977 null (vice president of development) null 10 22875270 1204470 2977 null (story producer) null 3 34572943 3175881 2977 null (researcher) null 10 23523736 3010112 2977 null (associate producer) null 3 34807912 1283294 2977 null (production assistant) null 10 25735322 2913596 2977 null null null 4 35273062 1467285 2977 null (animal trainer) null 10 26880882 44453 2977 null null null 5 35358334 3971223 2977 null (production coordinator) null 10 28223047 3373071 2977 null null null 6 2179445 293854 2977 534 null null 1 2298085 309091 2977 1 null null 1 10394207 1417428 2977 2381 null null 1 10556082 1442338 2977 436 (U.K. broadcast only) null 1 12089685 1658620 2977 2072314 null null 1 13722007 1871636 2977 2320963 null null 2 14407333 1958821 2977 39026 null null 2 14407334 1958821 2977 28033 null null 2 60862 9656 3228 19278 (voice) 15 1 18141402 2443462 3228 99274 (voice) 11 2 892289 125126 3228 212306 (voice) 4 1 18978952 2553967 3228 3002953 (voice) 2 2 892290 125126 3228 212307 (voice) 4 1 19121458 2572156 3228 295182 (voice) (as Tara Charendoff) 3 2 892291 125126 3228 212308 (voice) 4 1 19121459 2572156 3228 797172 (voice) (as Tara Charendoff) 3 2 892292 125126 3228 212309 (voice) 4 1 19121460 2572156 3228 2275242 (voice) (as Tara Charendoff) 3 2 892293 125126 3228 212310 (voice) 4 1 19931100 2673992 3228 2261562 (voice) 5 2 2313918 310784 3228 142071 (voice) 14 1 20643950 2747601 3228 null (executive producer) null 3 2980013 396894 3228 53312 null null 1 20864643 2767909 3228 null (executive producer) null 3 12118417 1663347 3228 186644 (voice) 6 1 21343285 534643 3228 null (executive producer) null 3 12118418 1663347 3228 2077148 (voice) 6 1 21860628 750213 3228 null (executive producer) null 3 12154871 1667114 3228 36325 (voice) null 1 25767954 1037906 3228 null (writer) null 4 12713062 1744984 3228 2230 (voice) (as Pamela Segall) 1 2 13802420 1879673 3228 2330316 (voice) 16 2 13802421 1879673 3228 649932 (voice) 16 2 16045276 2173288 3228 3129 (voice) (uncredited) null 2 20320074 2720370 3342 null (segment producer) null 3 1832 505 3342 53 (2000-2005) 1 1 21388533 2815148 3342 null (associate producer) null 3 14921889 2023792 3342 46773 (2000-2005) 2 2 21513831 2825107 3342 null (senior producer) null 3 31526365 3559310 3342 null null null 9 21613785 2833343 3342 null (senior executive producer) null 3 31615473 3565387 3342 null (associate director) null 10 21616087 640534 3342 null (supervising producer) nu

La table Role_type

In [0]:
#=============
# Role_Type
#=============
schema_role_type = "id INT, role STRING"

role_type = spark.read.csv(path = dir + "role_type.csv", schema = schema_role_type).persist()

role_type.createOrReplaceTempView("Role_Type")
#role_type.printSchema()

display(role_type)

id role 1 actor 2 actress 3 producer 4 writer 5 cinematographer 6 composer 7 costume designer 8 director 9 editor 10 miscellaneous crew 11 production designer 12 guest

La table Name affecte un identifiant id à une personne

In [0]:
#==============
# Name 
#==============
schema_name = """
  id int,
  name string,
  imdb_index string,
  imdb_id int,
  gender string,
  name_pcode_cf string,
  name_pcode_nf string,
  surname_pcode string,
  md5sum string
"""

name = spark.read.csv(path = dir + "name.csv", schema = schema_name).persist()

name.createOrReplaceTempView("Name")
#name.printSchema()

display(name)

id name imdb_index imdb_id gender name_pcode_cf name_pcode_nf surname_pcode md5sum 333 5, Johnny null null m J5 null null c845df6a62d46f897c7620f00f1e97a5 339 50 Cent null null m C53 null null faba8d4ac1b5880ef64a5de3ea7d1fa9 400 A El Rahim, Ahmed null null m A4653 A5346 A465 9698c31ec0eb8b38172ae89e8c67b028 457 A., Kodanda Rami Reddy null null m A2353 K3536 A 64223f8728574d3dce39126c365b5dc9 471 A., Randy null null m A653 R53 A b5301fd59f93e50ab8893e9b80e3a35a 624 Aaker, Lee null null m A264 L26 A26 e15546bb152954e379a3554c28125661 673 Aalto, Kari null null m A4326 K643 A43 8ad8a724a6ef5f40400c149162e12821 750 Aames, Willie null null m A524 W452 A52 f983dd44bb1392c1575dfe5ffb087e1b 763 Aamund, Asger null null m A5326 A2653 A53 0b6579030aba0724f451098c3bd533db 771 Aanensen, Peter null null m A5251 P3652 A525 1d4412351d4d6c5cfd6eb93eea053f25 840 Aarnseth, Marcus Mathias null null m A6523 M6253 null 24d6c97ecdf1a926ed20534c2a2f78bf 1044 Aarup-Sørensen, Malte null null m A6126 M4361 null 612642e95e61b1fc99e077a0ec2b52f2 1167 Abacan, Jose Mari null null m A1252 J2561 A125 06f8d8a8e7df8e7887ea7e7c7a671b8c 1246 Abadal, Ignasi null null m A1342 I2521 A134 ba871ea3beac14ecd206b51124a10126 1385 Abalos, Jason null null m A1425 J2514 A142 7c7a901c8c18e76d7425c26722d9cbdf 1386 Abalos, Jing null null m A1425 J5214 A142 62a10b012b2773ed13a5158f39701e90 1485 Abascal, Ramón null null m A1246 R5124 A124 012defeeb7876e0fb4a0bbe635ff49e0 1521 Abatantuono, Diego null null m A1353 D2135 null 91761d9dac3f6cf9bbd937caba55f695 1668 Abbas, Abdullah null null m A1213 A1341 A12 75d32dda4f991d7bd54a97acab864989 1736 Abbas, Waseem I null m A125 W2512 A12 c0adab4426668e18ae2ee62c6796dc26 1745 Abbas, Zaheer I null m A126 Z612 A12 16e68b0b1d9e999ac96449916bdeb726 1776 Abbasov, Gyunduz null null m A1212 G5321 A121 d9e62418630d32b057f90fa6821c56f7 1989 Abbott, Bud null null m A1313 B313 A13 21dbf662a05f4aa192d3d617f336044e 2038 Abbott, Fredric null null m A1316 F6362 A13 44061c42860f1265c7e48b614f855c80 2066 Abbott, Jamie I null m A1325 J513 A13 ea08b9950f7e1aa9579d2d2d3bf9a148 2133 Abbott, Philip null null m A1314 P413 A13 48cc3d70547e526ab8065f1fb1c13bb3 2366 Abdel, Sharif null null m A1342 S6134 A134 34064d8be229c24544130fe9934f708b 2796 Abduljawad, Anas null null m A1342 A5213 null 08165bc8d51d5487d342e923d3f213f6 2890 Abdullah, Rabih null null m A1346 R134 A134 3202740cdfb83fec7f23ea7c5bedefcc 3085 Abe, Roberto null null m A1616 R1631 A1 503103d264bdfa942b6a5a79913e6655 3121 Abe, Tôru null null m A136 T61 A1 139f60a00529b7048ff69a1f8b690e67 3369 Abele, Jim I null m A1425 J514 A14 2de3acc801c15caa5345844730ed1687 3392 Abeles, Nicolás null null m A1425 N2421 A142 a96ea6bd4554e7cf093f6b3049680fa8 3394 Abelesz, Israel null null m A1426 I2641 A142 cf3a5b3e5241b5a498790ee34c1da240 3454 Abella, Rey null null m A146 R14 A14 2bee781d1686fe753fdbed36d6d91362 3482 Abello, Jorge Enrique null null m A1426 J6256 A14 7ba58695b2486725ac40d6782f586541 3518 Abelson, Daniel null null m A1425 D5414 null cd795288ba9ef64371f5e6c17d8be617 3892 Abineri, Daniel null null m A1563 D5415 A156 8016db2f14217fee89f76d3fcae50767 3904 Abiodun, Afeez null null m A1351 A1213 A135 cabae8ef7c51db9ef218227456a101d6 3928 Abisror, Slade null null m A1262 S4312 A126 009df9615b73b9084d20e4297eb52f33 3963 Abkarian, Simon null null m A1265 S5126 null fa9a6747507dc95f1d7374a053d517c7 3976 Ablaza, Rolly null null m A1426 R4142 A142 3025e3e749d7b3588f9be95242192251 4024 Ablinger, Franz null null m A1452 F6521 null d91efb7c0ca2e5b242800d848749c2ed 4063 Abney, Kenny III null m A1525 K515 A15 56a455a16d75dfe24ecd7f91977941c9 4113 Abolo, J.R. null null m A1426 J614 A14 c8803d15512ec484f1910d77c491a3e2 4318 Abraham, Arthur II null m A1656 A6361 A165 515c4abe9606fa6822f24d00c28a492a 4356 Abraham, Falconer null null m A1651 F4256 A165 d05ba576ed0dd0588b28ee28b7ff5fc2 4382 Abraham, Jorge null null m A1652 J6216 A165 75dac53e723b965f6ded316577f70bb8 4406 Abraham, Morris null null m A1656 M6216 A165 3f8a23dbcb8

La table Person_Info

In [0]:
#==============
# Person_Info
#==============
schema_person_info = """
  id int,
  person_id int,
  info_type_id int,
  info string,
  note string
"""

person_info = spark.read.csv(path = dir + "person_info.csv", schema = schema_person_info).persist()
person_info.createOrReplaceTempView("Person_Info")

display(person_info)

id person_id info_type_id info note 302 333 33 (2012) Portlandia null 303 333 26 Martini-Connally, John null 304 333 20 Los Angeles, California, USA null 305 333 17 Has worked & studied alongside studio engineer giants like 'Kelley Baker (I)' (qv), 'Wayne Woods (I)' (qv), 'Paul Nelson (VIII)' (qv), 'John Neff' (qv), 'Russ Gorsline' (qv), 'Colin O'Neill (I)' (qv), 'Matt Meyer (II)' (qv), Brent Rogers, Randy Johnson, and 'Will Vinton' (qv). null 306 333 17 Bachelors in Digital Media Production from the Art Institute of Portland. null 307 333 17 Nephew of writer/director 'Richard Martini (I)' (qv). null 308 333 17 Related to former Texas Governor & U.S. Secretary of the Treasury 'John Connally (I)' (qv). null 309 333 21 7 September 1984 null 310 339 37 "Big Fish" (Greece), 4 June 2006, Iss. 28 null 311 339 37 "Hitkrant" (Netherlands), 19 March 2005, Iss. 11 null 312 339 37 "The Source" (USA), October 2003, Iss. 169 null 313 339 37 "Breakout!" (Netherlands), 7 August 2003, Iss. 33 null 314 339 37 "Dub" (USA), 2003, Iss. 15 null 315 339 25 Single: "In Da Club" (2003) null 316 339 25 Single: "P.I.M.P." (2003) null 317 339 25 Music video for 'Lloyd Banks' (qv): "On Fire" null 318 339 25 Music video for 'Lloyd Banks' (qv): "I'm So Fly" (also co-director). null 319 339 25 Music video for 'Young Buck' (qv): "Shorty Wanna Ride" null 320 339 25 Music video for 'Lloyd Banks' (qv): "Karma" null 321 339 25 Music video for 'Young Buck' (qv): "Let Me In" null 322 339 25 Music video for 'Eminem' (qv): "Like Toy Soldiers" null 323 339 25 Music video for 'Game' (qv): "How We Do" null 324 339 25 Album: "Get Rich or Die Tryin'," Shady/Aftermath/Interscope/Universal Records 493 544, 2003. null 325 339 25 Music video for 'Eminem' (qv): "Sing for the Moment" null 326 339 25 Album: "The Massacre," Shady/Aftermath/Interscope/Universal Records 210 388, 2005. null 327 339 25 Single: "Candy Shop" (March 2005) null 328 339 25 Single: "Disco Inferno" (2005) null 329 339 25 Single: "How We Do" (2005) null 330 339 25 Album: "Power of the Dollar" (1999) (unreleased) null 331 339 25 Album: "Guess Who's Back?" (2002) null 332 339 25 2005: TV commercial for Reebok. null 333 339 25 Album: "Just a Lil Bit", 2005. null 334 339 25 Single: "Just a Lil Bit" (May-June 2005) null 335 339 25 2005: Directed music video for Olivia feat. 'Lloyd Banks' (qv), "Twist It". null 336 339 25 2005: Public service announcement for The ONE Campaign [www.one.org] null 337 339 25 Music video for 'Game' (qv): "Hate It Or Love It" null 338 339 25 Music video for 'Tony Yayo' (qv): "So Seductive" null 339 339 25 Music video for 'Young Buck' (qv): "Look At Me Now/Bonafide Hustler" null 340 339 25 Music video for Olivia: "Twist It" null 341 339 25 Appears in 'Tony Yayo' (qv)'s video "Curious" (2005) null 342 339 25 2006: Print ad for Glacéau vitamin water. null 343 339 25 Music video for 'Ciara (I)' (qv): "Can't Leave 'Em Alone" null 344 339 25 Album: "Curtis," Shady/Aftermath/Interscope/Universal Records 173 340, 2007. null 345 339 25 TV commercial for Vitamin Water null 346 339 25 Music video for Eminem: "We Made You" null 347 339 25 Music video for Wisin & Yandel: "Mujeres In The Club" null 348 339 25 (2011) Music video for Jeremih: "Down On Me" null 349 339 25 (2011) Music video for Nicole Scherzinger: "Right There" null 350 339 28 Interscope null 351 339 28 Fiddy null 352 339 28 Boo Boo null 353 339 35 "Parade" (USA), 27 June 2010, pg. 2, by: Walter Scott, "Walter Scott asks...50 Cent" null 354 339 35 "Süddeutsche Zeitung" (Germany), 30 June 2007, by: Jonathan Fischer, "50 Cent über Verantwortung" null 355 339 35 "Big Fish" (Greece), 4 June 2006, Iss. 28, pg. 44-47, by: Lynley Dwight, "Otan enas andras einai gnostos ginetai issaxios me mia goiteftiki gineka" null 356 339 35 "Stuff" (USA), November 2005, Vol. 8, Iss. 11, pg. 118-119, by: Sean Fennessey, "50 Cent Sees the Light" null 357 339 35 "Maxim" (USA), November 2005, Vol. 9, Iss. 11, pg. 81, "50's Sense: He's got a new movie, a video

La table Movie_Companies

In [0]:
#==============
# Movie_Companies
#==============
schema_movie_companies = """
    id int,
    movie_id int,
    company_id int,
    company_type_id int,
    note string
"""

movie_companies = spark.read.csv(path = dir + "movie_companies.csv", schema = schema_movie_companies).persist()

movie_companies.createOrReplaceTempView("Movie_Companies")
#movie_companies.printSchema()

display(movie_companies)

id movie_id company_id company_type_id note 1318 3342 216 1 (2000) (USA) (TV) 1319 3342 217 1 (200?) (Japan) (TV) 1454 3981 46 1 (2009) (Hungary) (TV) 2889 8413 423 1 (2007) (Japan) (DVD) 2890 8413 49 1 (1987-1990) (USA) (TV) (original airing) 2891 8413 428 1 (2010) (USA) (DVD) 1276676 8413 71104 2 (producer) 1276677 8413 71105 2 (in association with) 4284 9005 21 1 (2010) (Australia) (TV) 4285 9005 49 1 (2010) (USA) (TV) 4286 9005 468 1 (2010) (Canada) (TV) 4287 9005 466 1 (2011) (Hungary) (TV) (M1) 4288 9005 31 1 (2010) (Netherlands) (TV) (RTL7) 4289 9005 469 1 (2010) (Germany) (TV) 4290 9005 459 1 (2010) (UK) (TV) 1277276 9005 424 2 null 1277277 9005 71124 2 null 1277278 9005 71123 2 (in association with) 1277565 9769 71146 2 null 6820 19610 265 1 (2009) (USA) (TV) 6821 19610 468 1 (2009) (Canada) (TV) 6822 19610 252 1 (2009) (Netherlands) (TV) 6823 19610 292 1 (2009) (Germany) (TV) 6824 19610 115 1 (2009) (Ireland) (TV) (RTÉ2) 6825 19610 164 1 (2009) (Hungary) (TV) 1279951 19610 598 2 null 1279952 19610 71363 2 null 7333 20786 754 1 (2007) (worldwide) (all media) 7334 20786 702 1 (2007) (worldwide) (video) (internet) 7335 20786 2 1 (2007) (worldwide) (video) (internet) 7336 20786 756 1 (2007) (worldwide) (video) (internet) 1280222 20786 754 2 null 7734 25679 27 1 (1965) (UK) (TV) 1280636 25679 27 2 null 7932 26805 139 1 (2004) (UK) (TV) 1280989 26805 71465 2 null 8439 31117 914 1 (1999-) (USA) (video) (VHS) 1281646 31117 71544 2 null 1281647 31117 3286 2 null 8585 32231 160 1 null 1281804 32231 62666 2 null 9749 34353 323 1 (1992-) (Germany) (TV) 9800 34743 160 1 (1960) (USA) (TV) 9834 34777 160 1 (1960) (USA) (TV) 1283021 35274 71703 2 null 10447 37369 699 1 (2008) (USA) (DVD) 1283485 38776 6083 2 null 10743 38999 643 1 (1983) (Spain) (TV) 1284766 38999 643 2 null 1284003 39310 9884 2 null 1284451 39760 9884 2 null 11118 40858 19 1 (1971) (USA) (TV) 11119 40858 145 1 (2010) (USA) (DVD) 1285231 40858 71768 2 null 1285232 40858 71767 2 null 1285233 40858 1284 2 null 11184 40962 6 1 (1987) (USA) (TV) 11359 42096 1164 1 (2008) (worldwide) (all media) 11603 42903 1186 1 (2007) (Russia) (TV) 1286332 42903 8216 2 null 13341 52038 196 1 (2002) (Sweden) (DVD) 13342 52038 197 1 (1982) (Sweden) (TV) 1288250 52038 6934 2 null 15130 54523 6 1 (1976) (USA) (TV) 15131 54523 34 1 (2012) (USA) (DVD) (DVD-R) 1289414 54523 72112 2 null 1289415 54523 11 2 null 16323 59975 284 1 (2011) (USA) (TV) 1290608 59975 71330 2 null 1291153 62975 72246 2 null 17034 64421 166 1 (2010) (Philippines) (TV) 1291348 64421 166 2 null 1292000 68289 376 2 null 1292061 68350 376 2 null 17639 70568 49 1 (2009) (USA) (TV) 1292490 71478 72315 2 null 18159 72691 517 1 (2009) (Hungary) (TV) 18824 74550 1684 1 (USA) (laserdisc) 18825 74550 1685 1 (USA) (DVD) 18826 74550 1685 1 (USA) (VHS) 18827 74550 312 1 (1987) (USA) (TV) (broadcast premiere) 1293970 74550 72400 2 null 19062 75086 1744 1 null 19063 75086 133 1 (1993) (Japan) (TV) 19064 75086 312 1 null 19255 75484 1783 1 (2012) (USA) (TV) 1294464 75484 2413 2 null 19380 76695 1244 1 (2005) (Mexico) (TV) 1294636 76695 1244 2 null 19548 78022 27 1 (UK) (TV) 20066 81053 293 1 (2008) (Germany) (DVD) 20067 81053 294 1 (2008) (Germany) (DVD) 1295319 81053 72604 2 null 21150 85610 789 1 (2009) (Canada) (TV) 1297299 85610 72716 2 null 1297300 85610 789 2 null 1297301 85610 72715 2 null 1297403 85745 21107 2 null 1297588 86268 72735 2 null 21704 91638 27 1 (2006) (UK) (TV) (BBC1) 1298020 92334 69728 2 null 1282326 92467 1008 2 null 1282480 92630 1008 2 null 22007 93326 6 1 (1974) (USA) (TV) 1298216 93326 46856 2 null 23341 99302 6 1 (1962) (USA) (TV) 1299729 99302 70905 2 null 24332 102724 166 1 (2012) (Philippines) (TV) 1300589 102724 166 2 null 24498 103461 6 1 (2001) (USA) (TV) 25207 104215 6 1 (2008) (USA) (TV) 25838 105191 6 1 (2002) (USA) (TV) 25926 105536 6 1 (2005) (USA) (TV) 26637 107616 59 1 (2004) (Netherlands) (DVD) 26638 107616 31 1 (2004) (Netherlands) (TV) (RTL4) 26639 107616 215 1 (2004) (Belgium) (TV) (origi

La table Company_Name

In [0]:
schema_company_name = """
    id int,
    name string,
    country_code string,
    imdb_id int,
    name_pcode_nf string,
    name_pcode_sf string,
    md5sum string
"""

company_name = spark.read.csv(path = dir + "company_name.csv", schema = schema_company_name)
company_name.createOrReplaceTempView("Company_Name")
#company_name.printSchema()

display(company_name)

id name country_code imdb_id name_pcode_nf name_pcode_sf md5sum 1 E! Entertainment Television [us] null E5363 E5363 ddc1ca3453a33526ad931106cb60d004 2 YouTube [us] null Y31 Y312 3bd77ab33669d8883d345ee754928caf 4 5* [gb] null null G1 2c0b57f4db6ba181ca8e7414284e9d35 5 Canadian Television (CTV) [ca] null C5353 C5353 7bde1000f06906373c3ae6a48d981511 6 Columbia Broadcasting System (CBS) [us] null C4516 C4516 7ae3ee174d2d4b06fc3d2ba6d7dc2fab 7 Nine Network Australia [au] null N5362 N5362 70a4657ea90ca544e4071e363774cc7c 8 Veronica [nl] null V652 V6525 28f313ed51c6f708e6755e2d5d34f0a3 9 Warner Channel Latin America [br] null W6562 W6562 eb1f896ee609e97cfbfb007f3de1afa5 10 Lorimar Telepictures [us] null L6563 L6563 6c941a84e38309ddf60871f4b76d8b53 11 Warner Bros. Television [us] null W6561 W6561 259d3edf9bdf0b20fc2db3e494113e99 12 A&E Television Networks [us] null A3412 A3412 0356ba010eec8b5688016a416aa645ba 13 Alliance Atlantis Broadcasting [ca] null A4523 A4523 10e18651971623d9f47cdc232d506796 15 Music Television 2 (MTV2) [us] null M2341 M2341 666169b92953bf6e8bc56df65473fda5 16 Music Television (MTV) [us] null M2341 M2341 3a1562902489f41a8a765371bce891fc 17 Food Network [us] null F3536 F3536 eef50373f7481373a5cec644ec999a4c 18 CanWest Global Communications [ca] null C5232 C5232 e15a00a401fe8309f381060356fd1411 19 National Broadcasting Company (NBC) [us] null N3541 N3541 9bb2ebf35b863c1467dee49d0b842952 20 MTV Networks [us] null M3153 M3153 f6d438e7b8b5a57ab97cbfc8e699e092 21 7 Network [au] null N362 N362 5b24f1569223d10d91fc66a133453abb 23 Paramount Television null null P6534 null 5baa812ba8256a9ca88c64b5aa493a5c 27 British Broadcasting Corporation (BBC) [gb] null B6321 B6321 f0a8c6e88a8c60d51ecaf3dedd9c2ef7 29 Pan Vision Oy [fi] null P5125 P5125 7c35599a7709c69338e1681bef8d0f72 30 Polyband [de] null P4153 P4153 1755c65dc5584890618bf7e357724639 31 RTL Entertainment [nl] null R3453 R3453 ce47054bc659e20dc047dddc15b1e72c 32 Televisie Radio Omroep Stichting (TROS) [nl] null T4126 T4126 16ceaeb698c1719048717c95947b0a03 33 Warner Home Video [nl] null W6565 W6565 d45bd8c0e87dfe3a2308925145fe8da2 34 Warner Home Video [us] null W6565 W6565 ccd32c6074495b83d1a78a9d2d11fdf8 36 CanWest Global Television Network [ca] null C5232 C5232 4338bbba86ec27b348505b82f7dcf276 38 Vitaya [be] null V3 V31 8360ed2df2389933bb79aaf92885c9b0 39 BBC Scotland [gb] null B1234 B1234 a7c27ba4a430484f65eed0c833dc68de 42 Filmbox HD [hu] null F4512 F4512 0df0354624485e95c2db77d189a9c396 44 Fremantle Media [gb] null F6534 F6534 754e1382d9218d76aee55257e0cda2d2 45 Poén! [hu] null P5 P5 8e5308634f515bebd61f5c68cc9d1415 46 RTL Klub Televízió [hu] null R3424 R3424 065f5fcf2db44545cbedb56fc4da8cc3 47 Sorozat [hu] null S623 S623 a5bd1c13b780c6635f59c9ec29405bca 49 Fox Network [us] null F2536 F2536 b65a0ae6b633a2f8f76de6ead49432ab 50 Sony Pictures Home Entertainment [be] null S5123 S5123 157c08c01f40725b28691bc27b78dc1c 51 Sony Pictures Home Entertainment [nl] null S5123 S5123 40deb8635be2c9907db1775d1e67ab73 52 Sony Pictures Home Entertainment [us] null S5123 S5123 1884e3668cacc1ccc2c45c3d472cd3e6 53 TV3 [ee] null T1 T1 73fbc41b12cde814c6baea5e99db3f37 54 Comedy Central Deutschland [de] null C5325 C5325 b42aa09812e78d9725b1334f4a0def49 55 Radio Télévision Belge Francophone (RTBF) [be] null R3412 R3412 640c4bb24d6925b5af5c904b53cb029c 56 TPS Star [fr] null T1236 T1236 02741b8301c06ddae49a25f81bfeb8e7 57 Spike TV [us] null S1231 S1231 f4544a8511d71f73cae02c5ce284ee76 59 Bridge Entertainment Group [nl] null B6325 B6325 8e5885ffd4a85044f74ae3877b051ee5 60 Katholieke Radio Omroep (KRO) [nl] null K3426 K3426 243e1a4b97cf554d142c3f9bbdb80835 61 Video Film Express [nl] null V3145 V3145 df3920ecd24dfe3b6eeaaf21ecfcef77 63 Verenigde Arbeiders Radio Amateurs (VARA) [nl] null V6523 V6523 32f57981e06a16543f419a25d354860f 64 Televisió de Catalunya (TV3) [es] null T4123 T4123 914ebde85366ae2077f6b17ca6a55ac0 67 Sat.1 [de] null S3 S3 2ceba90ea3a55dec156491f01ebf21a2 68 Westdeutscher Rundf

La table Company_type

In [0]:
#==============
# Company_Type
#==============
schema_company_type = "id INT, kind STRING"

company_type = spark.read.csv(path = dir + "company_type.csv", schema = schema_company_type).persist()
company_type.createOrReplaceTempView("Company_Type")
#company_type.printSchema()

display(company_type)

id kind 1 distributors 2 production companies 3 special effects companies 4 miscellaneous companies

In [0]:
%sql
create or replace temp view TitleDetail as
select t.id, t.title, t.production_year, k.kind, it.info as property, m.info as value
from Title t, Movie_Info m, Info_type it, Kind_Type k
where t.id = m.movie_id 
and m.info_type_id = it.id
and t.kind_id = k.id
;

select * 
from TitleDetail t

id title production_year kind property value 13 Intro: By My Side 2012 episode release dates Italy:29 March 2012 434 Brand in Mokum 2013 episode release dates Netherlands:7 January 2013 1680 A Tiny Problem in the Kitchen 2011 episode release dates USA:11 May 2011 1680 A Tiny Problem in the Kitchen 2011 episode release dates USA:11 May 2011 1841 (2005-03-20) 2005 episode release dates Spain:20 March 2005 2907 (2002-09-28) 2002 episode release dates Spain:28 September 2002 2977 Death: The Gift That Lasts Forever 2011 episode release dates USA:22 August 2011 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode release dates USA:27 September 1997 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode quotes Two-Tone: [watches Nanny set a yard sale box down] Yard sales! I love yard sales! Actually I hate yard sales, the pros of a yard sale are the great bargains but the cons of a yard sale are that everything is used, eww yuck::Cadpig: Two-Tone... FOCUS! 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode quotes Rolly: Anybody want a peanut?... What? It's not like I've offered you some of my food before. Okay, so it's been a while. 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode quotes Cadpig: Uh-oh! I'm having an out-of-bubble experience! 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode quotes Two-Tone: Hi, Mooch. Beautiful morning, isn't it?::Mooch: It was. I can't see it anymore! 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode quotes Two-Tone: Oh, Mooch? I just came by to say to you, I have nothing to say to you. If I had anything to say to you, I'd say it to Lucky, my date tonight at the dance.::Mooch: Say what? You always go out with me!::Two-Tone: Correction. Used to go with you, but you didn't ask me; Lucky did. 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode quotes Two-Tone: Don't hide, Lucky. I like your new look.::Lucky: No, you don't. Mooch is right. You don't want to be seen with me.::Two-Tone: Yes, I do! You're still Lucky. I think you're cool in any color.::Lucky: Really?::Two-Tone: Yeah. 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode quotes Rolly: Hey, watch where you're going, you clumsy box! 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode quotes Cadpig: No glitz, no glory. 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode quotes Lucky: The farm looks fantastic! Just looking at it makes me feel so... itchy!::Cadpig: What are you so itchy about?::Lucky: I'm itching to go to the dance with Two-Tone.::Cadpig: Someone's been bitten by the puppy love bug.::Lucky: Well, that explains why I itch... but does it explain why I hear music? 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode quotes Two-Tone: [to Mooch] I just came by here to say to you that I have nothing to say to you. If I had anything to say to you, I'd say it to Lucky... my date tonight at the dance! 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode quotes Two-Tone: Yard sales? I love yard sales! Actually, I hate yard sales. The pros of a yard sale are the bargains, but the cons of a yard sale are that the items are used! Ugh!::Cadpig: Two-Tone? Focus! 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode quotes Lucky: Where did you learn about this?::Spot: I'm Professor Egghead Science Over-Easy! 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode quotes Two-Tone: Hi, Mooch. Beautiful morning, isn't it?::Mooch: It was! I can't see it anymore! 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode quotes Lucky: I look like a big wad of bubble gum.::Rolly: Then why'd you dye yourself pink? You shoulda picked another color! 3228 He Followed Me Home/Love 'Em and Flea 'Em 1997 episode quotes Spot: How do you hide an elephant?::Rolly: Maybe we can put him on wheels and disguise him as a vacuum cleaner.::Spot: Or stick little magnets on him and pretend he's a refrigerator.::Cadpig: Or put a saddle on his back and pretend he's 

In [0]:
%sql
cache table TitleDetail

In [0]:
%sql
create or replace temp view NameDetail as
select n.id, n.name, n.gender, i.info as property, p.info as value
from Name n, Person_Info p, Info_type i
where n.id = p.person_id
and p.info_type_id = i.id
;
 
select * 
from NameDetail n

id name gender property value 333 5, Johnny m where now (2012) Portlandia 333 5, Johnny m birth name Martini-Connally, John 333 5, Johnny m birth notes Los Angeles, California, USA 333 5, Johnny m trivia Has worked & studied alongside studio engineer giants like 'Kelley Baker (I)' (qv), 'Wayne Woods (I)' (qv), 'Paul Nelson (VIII)' (qv), 'John Neff' (qv), 'Russ Gorsline' (qv), 'Colin O'Neill (I)' (qv), 'Matt Meyer (II)' (qv), Brent Rogers, Randy Johnson, and 'Will Vinton' (qv). 333 5, Johnny m trivia Bachelors in Digital Media Production from the Art Institute of Portland. 333 5, Johnny m trivia Nephew of writer/director 'Richard Martini (I)' (qv). 333 5, Johnny m trivia Related to former Texas Governor & U.S. Secretary of the Treasury 'John Connally (I)' (qv). 333 5, Johnny m birth date 7 September 1984 339 50 Cent m magazine cover photo "Big Fish" (Greece), 4 June 2006, Iss. 28 339 50 Cent m magazine cover photo "Hitkrant" (Netherlands), 19 March 2005, Iss. 11 339 50 Cent m magazine cover photo "The Source" (USA), October 2003, Iss. 169 339 50 Cent m magazine cover photo "Breakout!" (Netherlands), 7 August 2003, Iss. 33 339 50 Cent m magazine cover photo "Dub" (USA), 2003, Iss. 15 339 50 Cent m other works Single: "In Da Club" (2003) 339 50 Cent m other works Single: "P.I.M.P." (2003) 339 50 Cent m other works Music video for 'Lloyd Banks' (qv): "On Fire" 339 50 Cent m other works Music video for 'Lloyd Banks' (qv): "I'm So Fly" (also co-director). 339 50 Cent m other works Music video for 'Young Buck' (qv): "Shorty Wanna Ride" 339 50 Cent m other works Music video for 'Lloyd Banks' (qv): "Karma" 339 50 Cent m other works Music video for 'Young Buck' (qv): "Let Me In" 339 50 Cent m other works Music video for 'Eminem' (qv): "Like Toy Soldiers" 339 50 Cent m other works Music video for 'Game' (qv): "How We Do" 339 50 Cent m other works Album: "Get Rich or Die Tryin'," Shady/Aftermath/Interscope/Universal Records 493 544, 2003. 339 50 Cent m other works Music video for 'Eminem' (qv): "Sing for the Moment" 339 50 Cent m other works Album: "The Massacre," Shady/Aftermath/Interscope/Universal Records 210 388, 2005. 339 50 Cent m other works Single: "Candy Shop" (March 2005) 339 50 Cent m other works Single: "Disco Inferno" (2005) 339 50 Cent m other works Single: "How We Do" (2005) 339 50 Cent m other works Album: "Power of the Dollar" (1999) (unreleased) 339 50 Cent m other works Album: "Guess Who's Back?" (2002) 339 50 Cent m other works 2005: TV commercial for Reebok. 339 50 Cent m other works Album: "Just a Lil Bit", 2005. 339 50 Cent m other works Single: "Just a Lil Bit" (May-June 2005) 339 50 Cent m other works 2005: Directed music video for Olivia feat. 'Lloyd Banks' (qv), "Twist It". 339 50 Cent m other works 2005: Public service announcement for The ONE Campaign [www.one.org] 339 50 Cent m other works Music video for 'Game' (qv): "Hate It Or Love It" 339 50 Cent m other works Music video for 'Tony Yayo' (qv): "So Seductive" 339 50 Cent m other works Music video for 'Young Buck' (qv): "Look At Me Now/Bonafide Hustler" 339 50 Cent m other works Music video for Olivia: "Twist It" 339 50 Cent m other works Appears in 'Tony Yayo' (qv)'s video "Curious" (2005) 339 50 Cent m other works 2006: Print ad for Glacéau vitamin water. 339 50 Cent m other works Music video for 'Ciara (I)' (qv): "Can't Leave 'Em Alone" 339 50 Cent m other works Album: "Curtis," Shady/Aftermath/Interscope/Universal Records 173 340, 2007. 339 50 Cent m other works TV commercial for Vitamin Water 339 50 Cent m other works Music video for Eminem: "We Made You" 339 50 Cent m other works Music video for Wisin & Yandel: "Mujeres In The Club" 339 50 Cent m other works (2011) Music video for Jeremih: "Down On Me" 339 50 Cent m other works (2011) Music video for Nicole Scherzinger: "Right There" 339 50 Cent m nick names Interscope 339 50 Cent m nick names Fiddy 339 50 Cent m nick names Boo Boo 339 50 Cent m interviews "Parade" (USA), 27 June 2010, pg. 2, by: Walt

In [0]:
%sql
cache table NameDetail;

# Tâche 1
#### Restructurer la base de manière à définir des relations plus spécifiques
Dans cette tache, nous allons representer chaque propriété par une table.

A partir de la première vue donnant des informations détaillées sur les oeuvres (TitleDetail), nous allons créer les tables suivantes:
  - "Langue" contient les langues d'une oeuvre
  - "Genre" contient le genre d'une oeuvre.
  - "Budget" contient les informations quantité et devise.
  - "Admissions" contient le nombre d'entrées dans un pays pour un film à une date.
  - "Release" contient les informations liées à la sortie d'une oeuvre: le pays de sortie, la date de sortie 
  
A partir de la deuxième vue donnant des informations détaillées sur les personnes (NameDetail), nous allons créer les tables suivantes:
  
  - "Person" contenant le date de naissance, le pays de naissance et la date de décés d'une personne.
  - "Article" contenant l'année de publication d'un article sur une personne  dans un magazine
  - "Salary" contient le salaire (quantité et devise) perçu par une personne pour un film, le nom du film ainsi que l'année
  - "Interview" contenant l'année et le pays d'une interview faite par une personne ainsi que le nom du média

### La table Langue

In [0]:
%sql
create or replace temp view Langue as
select id as id_movie,title as title_movie,value as language from TitleDetail where property="languages";
 
select * from Langue
limit 10

id_movie title_movie language 3342 106 & Park Top 10 Live English 3981 Ärzte für Südafrika German 9005 Day 8: 7:00 p.m.-8:00 p.m. English 9376 (#1.36) Danish 12020 (#1.13) Japanese 14092 (#1.7) English 19610 Hello, Goodbye, Amen English 22983 (#1.40) Portuguese 25679 The Third Person English 26805 A Place by the Sea English

### La table Genre

In [0]:
%sql
create or replace temp view Genre as
select id as id_movie,title as title_movie,value as genre from TitleDetail where property="genres";
 
select * from Genre

id_movie title_movie genre 3342 106 & Park Top 10 Live Music 26805 A Place by the Sea Documentary 31117 A Última Semana Biography 31117 A Última Semana Drama 31117 A Última Semana Family 31117 A Última Semana History 32231 Boys Will Be Boys Drama 34353 Abenteuer Zoo Documentary 74550 Directed by William Wyler Documentary 75086 Dottie Drama 75086 Dottie Family 75484 American Weed Reality-TV 78022 An Evening at Home with Bernard Braden and Barbara Kelly Comedy 83387 Animal Cops: San Francisco Crime 83387 Animal Cops: San Francisco Documentary 107616 De Midasmoorden Crime 107616 De Midasmoorden Drama 114708 Australia's Worst Driver Reality-TV 116500 Aventuras Vascas Adventure 120158 Baaghe Mozaffar Comedy 124831 Balash Be-Yerushalayim Drama 126994 Banegi Apni Baat Drama 136133 When in Rome Comedy 138436 Beautiful You HDTV Talk-Show 138917 Gamen Crime 138917 Gamen Thriller 141781 Beit Sefer Chagavim Comedy 155963 Bij Dorus op visite Comedy 172170 Bonjour la France News 172170 Bonjour la France Talk-Show 192280 Böttinger Talk-Show 192293 Børneafdelingen Documentary 202528 Canada's Super Speller Family 202528 Canada's Super Speller Game-Show 202976 Canarias Noticias News 216018 Puppetman Comedy 216018 Puppetman Family 217158 Cedomir Ilic Drama 217936 Celebrity Countdown Game-Show 223010 Chapi-Chapo Animation 223010 Chapi-Chapo Family 223012 Chappelle's Show Comedy 223012 Chappelle's Show Music 224332 Chasing UFOs Reality-TV 228035 Chicaboom Family 229478 China Beach Drama 229478 China Beach War 237637 Cinema!!! Biography 251237 Code Blue: Savannah Documentary 260388 Con Trek Documentary 260388 Con Trek Sci-Fi 264018 Cook's Country from America's Test Kitchen Documentary 264786 Cop Shows Anonymous Comedy 298696 Baby Bible Bashers Documentary 302641 Dai noi kwan ying Action 302641 Dai noi kwan ying Drama 302641 Dai noi kwan ying History 308354 Danmarks klogeste barn Family 308354 Danmarks klogeste barn Game-Show 309672 Dark Season Adventure 309672 Dark Season Family 309672 Dark Season Sci-Fi 311970 Das Familiengericht Reality-TV 323468 De bende van Wim Adventure 323468 De bende van Wim Comedy 323468 De bende van Wim Reality-TV 326376 De rechtvaardige rechters Comedy 336958 Denise... aujourd'hui Comedy 355687 Die Modellbauer Documentary 355687 Die Modellbauer Reality-TV 356872 Die Schlager des Jahres Music 359804 Digital Life with Shelly Palmer Talk-Show 360969 Dinner Date Reality-TV 361817 Diplomci Comedy 377674 Don't Drive Here Reality-TV 381207 Down to Business with Josh Dirks Talk-Show 387261 Dramma d'amore Drama 392718 Dynaman Action 392718 Dynaman Adventure 392718 Dynaman Comedy 392718 Dynaman Sci-Fi 403980 Editor's Picks News 406757 Ein Sofa in Berlin - Tulpe und Conrady laden ein Reality-TV 406757 Ein Sofa in Berlin - Tulpe und Conrady laden ein Talk-Show 407889 El amor tiene cara de mujer Drama 407889 El amor tiene cara de mujer Romance 412272 El Dorado Action 412272 El Dorado Adventure 412272 El Dorado Fantasy 417274 El món d'Ariadna News 417274 El món d'Ariadna Talk-Show 417512 El pantano Drama 417512 El pantano Mystery 420371 El recuento de los daños Documentary 422409 El Smosh Comedy 427620 Ellinikes istories mystiriou kai fantasias Fantasy 427620 Ellinikes istories mystiriou kai fantasias Mystery 427620 Ellinikes istories mystiriou kai fantasias Sci-Fi 441066 Entrevista con Sarmiento Talk-Show 441991 Equitrekking Documentary 441991 Equitrekking History 441991 Equitrekking Sport 452264 Ett herrans liv Talk-Show 456217 Exit Documentary 460892 Fa cheng sin fung Crime 460892 Fa cheng sin fung Drama 462973 Fais pas ci, fais pas ça Comedy 475011 Faut pas rêver Documentary 475206 FBi Family 480515 Final Score Reality-TV 486474 Flying High Adventure 486474 Flying High Comedy 486474 Flying High Drama 493245 Fox Family High School Countdown Family 493245 Fox Family High School Countdown Music 504215 Fusion TV Music 512699 Gekai Hiiragi Matasaburô Drama 548667 Great Dinners of the World Reality-TV 550835 Grillen Comedy 555957 Gwor h

### La table Budget

In [0]:
%sql
create or replace temp view Budget as
with R0 as (select id as id_movie,title as title_movie,regexp_extract(value,"([0-9,]+)")as amount, regexp_extract(value,"([a-zA-Z$€£]+)") as currency
from TitleDetail where property = "budget") select id_movie,title_movie,cast(regexp_replace(amount,',','')as int) as amount,currency from R0;
 
select * from Budget

id_movie title_movie amount currency 141781 Beit Sefer Chagavim 130000 $ 172170 Bonjour la France 150000 € 237637 Cinema!!! 300000000 ITL 260388 Con Trek 12000 $ 264786 Cop Shows Anonymous 5000 $ 381207 Down to Business with Josh Dirks 650000 $ 504215 Fusion TV 250000 $ 548667 Great Dinners of the World 200 £ 811710 Lost & Found in Asia 2 15000 € 852293 Me & Mi Kru 120000 $ 871092 Mind of a Millionaire 750000 £ 877809 Mochileando 20000 $ 886516 MoreThanMusic 10000 $ 912681 Nanalan' 1500000 CAD 1059119 Quick Cuts 300000 £ 1077263 Regina 2000000 $ 1184142 Southern Home by Design 18000 $ 1296949 The Brothers 10000 £ 1408324 The Revolver 4 10000 CAD 1417866 The Simpsons 750000 $ 1472103 TimeChase 20000 CAD 1635519 11,830,420 2500 $ 1635662 12 Before Dark 100 $ 1638676 2006 Vans Protec Pool Party 100000 $ 1640310 3 Solitude 6000000 $ 1640360 3 Women 1500000 $ 1640436 3.14... 100000 $ 1640559 30 Seconds to Air: The Making of the Bill Cunningham Show 10000 $ 1641722 4D Man 240000 $ 1648164 A Face Fixed 2500 $ 1652314 A ma chère petite maman 5000 € 1654259 A Nightmare on Elm Street: The Dream Child 8000000 $ 1656394 A Round of Hope 250000 $ 1658722 A Thin Line Between Love and Hate 8000000 $ 1663199 Above as Below 225 £ 1663952 Acceptance 250000 £ 1665018 Action Hero 500000 $ 1666737 Adventure 3500000 $ 1669159 Agent Provocateur 5000 AUD 1670517 Ain't Misbehavin' 20000 £ 1670524 Ain't No Stoppin Me 200 NOK 1673570 Alex and Ro 150000 $ 1674408 Alice in Storageland 2000 $ 1677226 Alligator II: The Mutation 3000000 $ 1679902 Amazin' 5000 $ 1681402 American Rebel: The Dean Reed Story 350000 $ 1692359 Apocalyptic Adventure on the Eastern Frontier 3000 £ 1698254 Asi es la vida 40000 $ 1704921 Awaken 500 $ 1707518 Bacatete, donde se oye la guerra 200000 MXN 1710058 Bailen 58 1000 € 1711437 Ballyvaughan Story 500 $ 1714929 Basic Instinct 40000000 $ 1717143 Bearer's End 1200 ZAR 1718377 Bed 800 £ 1718540 Bedroom Politics 1000 £ 1720607 Believe It 130000 CAD 1721705 Benedict XVI: The Keys of the Kingdom 50000 € 1723850 Bettina 30000 $ 1723958 Betty on the Bed 4000 $ 1735949 Blood Ties 15000 $ 1737352 Blueberry Pancakes 2500 $ 1737364 Bluefield 100000 $ 1741200 Bordenia 8000 $ 1743177 Boy s tenyu 3. Posledniy raund 5000000 $ 1744255 Brave New World 80000 $ 1745294 Breathing Room 500000 $ 1747209 Broken Image 1000 $ 1759729 Car Trouble 2: Them's the Brakes 14000 $ 1763216 Catch-22 18000000 $ 1765358 Cereal Thriller 500000 CAD 1765860 Cha-Ci-Pe 42661 CZK 1776735 Circle of Iron 4000000 $ 1777174 CIS: Las Gidi 850000 $ 1777299 Citizen Hong Kong 425000 $ 1778419 Classic of Changes 5000 $ 1778844 Cleanse & Build Inner Qi 25000 $ 1782321 College Radio Day: A Documentary 5000 $ 1788698 Corazones de azúcar 1000 € 1791850 Crash 9000000 $ 1792571 Creation of the Humanoids: Green Screen Test 100 $ 1796721 Cundeamor 150000 $ 1797249 Curly Sue 25000000 $ 1806341 Das Paradies 3000 € 1808493 Day of the Spider 150 $ 1809437 De grotten van Han van Vloten 60000 € 1810763 De-Lovely 20000000 $ 1813911 Deep and Secret Things 100 $ 1814692 DeGeneration 500 $ 1819801 Der Mystische Edelmann 500 $ 1822340 Descendant of the First 5000 AUD 1825067 Devil's Tree 175000 $ 1825864 Diabolical Tales: Part II 400 $ 1837200 Doble sesión 200000 € 1839401 Domus 4000000 ITL 1848433 Duffy's Irish Circus 23000 $ 1848778 Dumb Movie Ways to Die 50 £ 1849184 Dupont Guy: The Schiz of Grant Avenue 7000 $ 1851367 E.V.P. 15000 £ 1861087 El mundo de Tomás 1200 ARS 1864691 Elf Bowling the Movie: The Great North Pole Elf Strike 6500000 $ 1868924 Enemies Closer 10000000 $ 1872701 Escape from Cassius 500 NZD 1873821 Essas Palavras 745 BRL 1876797 Everything Is Poetry Baby 65000 SEK 1878534 Expired 10000 $ 1889568 File Cabinet 28000 $ 1894758 Flip 100 CAD 1898655 Forever 35000 $ 1901169 Frank 18000000 $ 1905159 Frontal Lobe 30000 $ 1918459 Girl Walks Into a Bar 1000000 $ 1920097 Glass 4500 $ 1924677 Goodbye 200 $ 1924730 Goodbye Horses 7000 $ 1926073 Grace Is Gone 2000000 $ 1931020 Gun of the Falle

### La table Admissions

In [0]:
%sql
create or replace temp view Admissions as
with R1 as (with R0 as (select * from TitleDetail where property='admissions')
select id,title, element_at(split(value, ' '),1) as number ,element_at(split(value, ' '),2) as country, element_at(split(value, ' '),3) as day,
element_at(split(value, ' '),4) as month,element_at(split(value, ' '),5) as year
from R0)
select id as id_movie,title as title_movie,cast(regexp_replace(number,',','') as int) as number,regexp_extract(country,'([a-zA-Z]+)') as country,cast(regexp_extract(day,'([0-9]+)') as int)as day,
regexp_extract(month,'([a-zA-Z]+)') as month,cast(regexp_extract(year,'([0-9]+)') as int)as year  from R1;
 
select * from Admissions

id_movie title_movie number country day month year 1714929 Basic Instinct 4651563 France null null null 1714929 Basic Instinct 4406353 Germany 31 December 1992 1714929 Basic Instinct 1262687 Netherlands null null null 1723342 Best-Seller: El premio 21224 Spain null null null 1761387 Carrington 380687 France 4 July 1995 1791850 Crash 541663 France 3 September 1996 1791850 Crash 402103 France 6 August 1996 1791850 Crash 16548 Netherlands 31 December 1998 1791850 Crash 16537 Netherlands 1 January 1998 1791850 Crash 78535 Portugal 19 December 1996 1791850 Crash 75794 Portugal 12 December 1996 1791850 Crash 72621 Portugal 5 December 1996 1791850 Crash 67629 Portugal 28 November 1996 1791850 Crash 61232 Portugal 21 November 1996 1791850 Crash 53333 Portugal 14 November 1996 1791850 Crash 44531 Portugal 7 November 1996 1791850 Crash 32353 Portugal 31 October 1996 1791850 Crash 19569 Portugal 24 October 1996 1791850 Crash 10359 Portugal 10 October 1996 1791850 Crash 204526 Spain null null null 1857778 El bosque animado 16007 Netherlands 31 December 2003 1857778 El bosque animado 504258 Spain 10 August 2002 1861440 El otro árbol de Guernica 723416 Spain null null null 1866788 Empire Records 149 Spain null null null 1875462 European Vacation 67868 Sweden null null null 1882328 Familie 49096 Netherlands 31 December 2002 1882328 Familie 6047 Netherlands 31 December 2001 1916458 Ghost Dog: The Way of the Samurai 491893 France 16 November 1999 1916458 Ghost Dog: The Way of the Samurai 461905 France 9 November 1999 1916458 Ghost Dog: The Way of the Samurai 420613 France 2 November 1999 1916458 Ghost Dog: The Way of the Samurai 365989 France 26 October 1999 1916458 Ghost Dog: The Way of the Samurai 275082 France 19 October 1999 1916458 Ghost Dog: The Way of the Samurai 175191 France 12 October 1999 1916458 Ghost Dog: The Way of the Samurai 16653 Netherlands 31 December 2001 1916458 Ghost Dog: The Way of the Samurai 16353 Netherlands 31 December 2000 1926073 Grace Is Gone 2063 Netherlands 31 December 2008 1963001 Hufters & Hofdames 22954 Netherlands 31 December 1998 1963001 Hufters & Hofdames 22629 Netherlands 1 January 1998 1979737 In een Japanse stroomversnelling 305 Netherlands 31 December 2003 1979737 In een Japanse stroomversnelling 246 Netherlands 31 December 2002 2005888 Julia 1843 Netherlands 31 December 2008 2046193 La próxima estación 448643 Spain null null null 2053175 Lars and the Real Girl 9802 Netherlands 31 December 2008 2062042 Le salaire du péché 1340747 France null null null 2069604 Les têtes brûlées 255914 Spain null null null 2074956 Ligue Story 1328813 Spain null null null 2082605 Lord of the Flies 63076 Spain null null null 2084351 Los últimos de Filipinas 29966 Spain null null null 2099290 Mammoth 11732 Netherlands 31 December 2009 2142410 Na-eui No-lae-neun 380 South null null 2142410 Na-eui No-lae-neun 249 South null null 2168956 Oechul 23307 France null null null 2212490 Posición viciada 15000 Colombia null null null 2245599 Ritzar bez bronya 712161 Bulgaria null null null 2294518 Slumdog Millionaire 536788 Netherlands 31 December 2009 2303248 Source Code 452681 Spain null null null 2388912 The Love Bug 751497 Hungary null null null 2418323 The Taking of Pelham 1 2 3 176464 Netherlands 31 December 2009 2460328 Umorismo in nero 79032 Spain null null null 2463424 Una monja y un Don Juan 933859 Spain null null null 2465773 Une exécution ordinaire 150295 France 16 March 2010 2517945 Zatôichi 89614 France 11 November 2003 1700217 Así es Galicia 41053 Spain null null null 1743323 Boys and Girls 343224 Spain 31 August 2002 1749300 Buddha's Lost Children 41218 Netherlands 31 December 2007 1749300 Buddha's Lost Children 33360 Netherlands 31 December 2006 1775030 Chugyeogja 1677 Netherlands 31 December 2009 1821034 Der Todesrächer von Soho 166553 Spain null null null 1859407 El extraño viaje 207733 Spain null null null 1872514 Esa maldita costilla 939595 Argentina null null null 1928518 Grev Axel 67440 Denmark 31 December 2002 

### La table Release

In [0]:
%sql
create or replace temp view Release as
with R1 as (with R0 as (select * from TitleDetail where property='release dates')
select id,title, element_at(split(value, ':'),1) as country ,element_at(split(value, ':'),2) as release_date from R0)
select id as id_movie,title as title_movie,country,element_at(split(release_date, ' '),1) as day,element_at(split(release_date, ' '),2) as month,element_at(split(release_date, ' '),3) as year from R1
;
 
select * from Release

id_movie title_movie country day month year 13 Intro: By My Side Italy 29 March 2012 434 Brand in Mokum Netherlands 7 January 2013 1680 A Tiny Problem in the Kitchen USA 11 May 2011 1680 A Tiny Problem in the Kitchen USA 11 May 2011 1841 (2005-03-20) Spain 20 March 2005 2907 (2002-09-28) Spain 28 September 2002 2977 Death: The Gift That Lasts Forever USA 22 August 2011 3228 He Followed Me Home/Love 'Em and Flea 'Em USA 27 September 1997 3342 106 & Park Top 10 Live USA September 2000 null 3345 (2001-08-23) USA 23 August 2001 3493 Brother J and Jibbs in the Building USA 18 August 2006 3544 Underground-Mainstreem Rappers Judging Freestyle Friday USA 17 September 2004 3981 Ärzte für Südafrika Germany 22 October 2008 3981 Ärzte für Südafrika Hungary 30 June 2009 5115 Duggars Movin' Out USA 16 February 2010 5410 (2005-09-11) USA 11 September 2005 6416 Leslie Jones/G. Thang/Corey 'Zooman' Miller USA 25 November 2005 6484 Fall Trends USA 19 September 2009 6799 Quote im Abseits - Merkel stoppt Frauen-Power Germany 7 February 2011 7169 (2006-12-26) France 26 December 2006 7430 (2005-08-26) USA 26 August 2005 7436 (2006-05-26) USA 26 May 2006 7946 Anaheim Ducks at the Pittsburgh Penguins USA October 2007 null 8031 Vancouver Canucks at Edmonton Oilers USA November 2007 null 8292 Brooke Lewis USA 1 June 2011 8413 Orpheus 3.3 USA 28 February 1988 9005 Day 8: 7:00 p.m.-8:00 p.m. Canada 18 January 2010 9005 Day 8: 7:00 p.m.-8:00 p.m. USA 18 January 2010 9005 Day 8: 7:00 p.m.-8:00 p.m. UK 31 January 2010 9005 Day 8: 7:00 p.m.-8:00 p.m. Australia 9 February 2010 9005 Day 8: 7:00 p.m.-8:00 p.m. Germany 15 March 2010 9005 Day 8: 7:00 p.m.-8:00 p.m. Netherlands 12 September 2010 9005 Day 8: 7:00 p.m.-8:00 p.m. Finland 21 September 2010 9005 Day 8: 7:00 p.m.-8:00 p.m. Hungary 8 December 2010 9005 Day 8: 7:00 p.m.-8:00 p.m. Japan 23 December 2010 9256 Chain Gang USA 6 May 1958 9376 (#1.36) Denmark 15 November 2007 9597 (1974-11-16) UK 16 November 1974 9769 Thomasville, Ga. USA 19 August 2004 10280 Country Style UK 25 February 1984 10331 Nightclub UK 11 February 1984 10750 Delivering the Goods USA 29 August 2009 11564 (#1.6) Australia 14 July 2012 12020 (#1.13) Japan 17 November 2010 12523 (1990-05-01) Spain 1 May 1990 12951 I Lalandia med Brian fra Singleliv Denmark 28 March 2011 12955 I London med Clemens Denmark 7 March 2011 13148 Alis Part II USA 17 November 2012 13242 Krystal's Courage USA 28 November 2009 13473 The Stranger You Know USA 2 February 2013 13475 The Untold Story of Caylee Anthony USA 17 October 2009 14092 (#1.7) UK 11 January 2006 14286 (2010-08-02) Portugal 2 August 2010 14601 Karateka USA 14 March 2010 14650 Resident Evil USA 26 July 2009 15064 (#4.35) Spain 17 May 2011 15765 A Lobbyist's Playbook/Operation Proper Exit/Andy Rooney USA 6 November 2011 16249 Ohio/Lifeline/The Pentagon's Ray Gun USA 3 March 2008 16604 The Next First Lady?/Here Comes the Girls/Toni Morrison USA 31 January 1999 17814 (1991-02-10) France 10 February 1991 17979 Amsterdamned Spain 2 May 1999 18330 (#1.2) Hungary 1999 null null 19610 Hello, Goodbye, Amen Canada 6 January 2009 19610 Hello, Goodbye, Amen USA 6 January 2009 19610 Hello, Goodbye, Amen Netherlands 16 June 2009 19610 Hello, Goodbye, Amen Germany 4 July 2009 19610 Hello, Goodbye, Amen Hungary 3 October 2009 19610 Hello, Goodbye, Amen Japan 19 June 2010 19610 Hello, Goodbye, Amen Afghanistan 28 May 2011 19920 The Case of the Missing Dog USA 30 October 2010 19920 The Case of the Missing Dog USA 23 October 2010 19980 (2007-12-19) Spain 19 December 2007 20154 Baby Ginn USA 7 October 2009 20159 Baby Gordon USA 18 October 2005 20434 Waste and Recycling UK 4 August 1990 20786 Marc Guggenheim & Scalped USA 22 July 2009 21133 Coming Ready or Not: Part 1 Australia 22 August 1982 21216 Fallen Idols: Part 2 Australia 1988 null null 21871 Things of Value: Part 1 Australia 6 July 1987 21964 Wings: Part 2 Australia 10 March 1992 22772 (#2.21) Spain 26 January 2011 22830 (#3.35) Spain 2 May 2012 22983 (#1.40) B

### La table Person

In [0]:
%sql
create or replace temp view Person as
with R1 as (with R0 as (select p1.id,p1.name, p1.value as birth_date,p2.value as death_date from NameDetail p1 left outer join NameDetail p2 on (p1.id=p2.id  and p2.property="death date") where p1.property="birth date"
) select id ,name ,regexp_extract(birth_date,'([0-9][0-9]? )',1) as birth_day,regexp_extract(birth_date,'([a-zA-Z]+)',1) as birth_month,
regexp_extract(birth_date,'([0-9][0-9][0-9][0-9])',1) as birth_year,regexp_extract(death_date,'([0-9][0-9]? )',1) as death_day,regexp_extract(death_date,'([a-zA-Z]+)',1) as death_month,regexp_extract(death_date,'([0-9][0-9][0-9][0-9])',1) as death_year from R0)
select r.id as id_person, r.name as name_person ,element_at(split(nd.value, ','),-1) as birth_country,cast(r.birth_day as int),r.birth_month,cast(r.birth_year as int),cast(r.death_day as int),r.death_month,cast(r.death_year as int)
from R1 r left outer join NameDetail nd on 
(r.id=nd.id and nd.property="birth notes");
 
select * from Person
 

id_person name_person birth_country birth_day birth_month birth_year death_day death_month death_year 1521 Abatantuono, Diego Italy 20 May 1955 null null null 1668 Abbas, Abdullah Syria 15 November 1906 3 November 1986 1989 Abbott, Bud USA 2 October 1895 24 April 1974 3121 Abe, Tôru Japan 28 March 1917 18 July 1993 3482 Abello, Jorge Enrique Colombia 28 February 1968 null null null 3892 Abineri, Daniel null 24 October 1958 null null null 4318 Abraham, Arthur USSR 20 February 1980 null null null 4523 Abrahams, Mort USA 26 March 1916 28 May 2009 4662 Abramoff, Jack USA 28 February 1958 null null null 5803 Accornero, Roberto Italy null 1957 null null null 6152 Achard, Marcel France 5 July 1899 4 September 1974 6466 Acker, Berko Germany 14 March 1945 1 December 1978 6740 Ackroyd, Jack UK 5 June 1890 null 1972 6892 Acosta, Christian USA 4 November 1987 null null null 7469 Adair, Robyn USA 11 February 1884 null February 1965 7555 Adam, Alfred France 4 April 1908 7 May 1982 7915 Adamo, Antonio Italy 30 July 1957 null null null 8393 Adams, Donald UK 20 December 1928 8 April 1996 8572 Adams, James Leland USA 7 February 1963 null null null 8692 Adams, Jonathan UK 14 February 1931 13 June 2005 9051 Adams, R.J. Canada 20 September 1946 null null null 9199 Adams, Shawn null 11 July null null null null 9407 Adamsdale, Will UK null 1974 null null null 9496 Adamson, Peter UK 16 February 1930 17 January 2002 9523 Adamson, Victor New Zealand 4 January 1890 9 November 1972 9544 Adamíra, Jirí Czechoslovakia 2 April 1926 14 August 1993 10263 Adeolu, Funso Nigeria 9 May 1968 null null null 10276 Ader, Bob USA 28 February 1952 null null null 10314 Aders, Johan Netherlands 23 December 1977 null null null 10895 Adler, Jerry USA 4 February 1929 null null null 11139 Adolph, Alexander Germany 10 November 1965 null null null 11201 Adonis, Adrian USA 15 September 1953 4 July 1988 11403 Adrian, Vulpe Romania 31 August 1983 null null null 11694 Aendenboom, Frank Belgium 24 October 1941 null null null 11784 Afanasev, Aleksandr null null 1917 null 1987 11972 Afman, Frans J. Netherlands 11 December 1933 4 May 2011 12053 Afonso, Yves France 13 February 1944 null null null 12915 Agirre, Ramón Spain null 1949 null null null 13218 Agosto, Ben USA 15 January 1982 null null null 13897 Aguilar, Luis Mexico 29 January 1918 24 October 1997 13977 Aguilar, Santiago Spain null 1899 null 1953 14356 Aguirresarobe, Javier Spain 10 October 1948 null null null 15021 Ahluwalia, Jassa UK 12 September 1990 null null null 15032 Ahlén, Emil Sweden 3 December 1984 null null null 15706 Ahola, Jouko Finland 1 December 1970 null null null 15862 Ahrle, Leif Sweden 10 June 1943 null null null 16264 Aijima, Kazuyuki Japan 30 November 1961 null null null 16503 Ainley, Anthony UK 20 August 1932 3 May 2004 16879 Aitken, Jonathan Ireland 30 August 1942 null null null 16897 Aitken, Spottiswoode UK 16 April 1867 26 February 1933 16926 Aittoniemi, Sulo Finland 11 July 1936 null null null 17303 Akagi, Keiichiro Japan 8 May 1939 21 February 1961 17579 Akbas, Hayati Turkey 1 December 1977 null null null 18099 Akin, Fatih West Germany 25 August 1973 null null null 19728 Al-Shennawi, Kamal Egypt 26 December 1921 22 August 2011 19856 Alabi, Anthony USA 16 February 1981 null null null 20322 Alan, Ray UK 18 September 1930 24 May 2010 20554 Alarcón, Pablo Argentina 9 September 1946 null null null 20644 Alaskey, Joe USA 17 April 1952 null null null 20889 Alba, R.D. Philippines 4 September 1978 null null null 21113 Albareda, Aleix Spain 5 November 1973 null null null 21273 Alberich Mexico 12 August 1982 null null null 21326 Albers, Hans Germany 22 September 1891 24 July 1960 21653 Albertini, Luciano Italy 30 November 1882 6 January 1945 21682 Alberto Moniz, Carlos Portugal 2 August 1948 null null null 21964 Albinet, Vasile null 12 February 1968 null null null 21992 Albiston, Arthur UK 14 July 1957 null null null 22060 Alborough, Roger UK 19 February 1953 null null null 22788 Alcott, John UK null 1931 28 Jul

### La table Article

In [0]:
%sql
create or replace temp view Article as
select id as id_person,name as name_person,regexp_replace(regexp_extract(value,'("(.*?)" )',1),'"',"")as magazine,cast(regexp_extract(value,'([0-9][0-9][0-9][0-9])',1)as int) as year,regexp_extract(value,'\\((.*?)\\)',1) as country from NameDetail where property='article';
 
select * from Article

id_person name_person magazine year country 1989 Abbott, Bud America in WWII 2011 USA 1989 Abbott, Bud Current Biography 1941 USA 4523 Abrahams, Mort The Independent 2009 UK 7915 Adamo, Antonio Inside 2003 Austria 9051 Adams, R.J. Library Journal 1999 USA 9051 Adams, R.J. Library Journal 1999 U.S. States 11972 Afman, Frans J. ScreenDaily.com 2011 USA 11972 Afman, Frans J. Hollywood Reporter 2011 USA 11972 Afman, Frans J. ScreenDaily.com 2011 USA 11972 Afman, Frans J. Los Angeles Times 1985 USA 16503 Ainley, Anthony The Times 2004 UK 16503 Ainley, Anthony The Guardian 2004 UK 20322 Alan, Ray The Independent 2010 UK 21326 Albers, Hans California Staats -Zeitung 2004 USA 23191 Alderman, Ted The Scream 2005 UK 24156 Alerme, André Dictionnaire du Cinéma/Les Acteurs 2007 France 24576 Alexander, Bjørn VG 2012 Norway 24576 Alexander, Bjørn Avisa Nordland 2012 Norway 24576 Alexander, Bjørn Adressa.no 2012 Norway 24576 Alexander, Bjørn P5 Radio 2012 Norway 24576 Alexander, Bjørn P4 Radio 2012 Norway 24576 Alexander, Bjørn Ranablad.no 2012 Norway 24576 Alexander, Bjørn Rana Blad 2012 Norway 24576 Alexander, Bjørn Nettavisen- Side2 2012 Norway 24576 Alexander, Bjørn Adresseavisen 2012 Norway 24576 Alexander, Bjørn Romerikes blad 2012 Norway 24576 Alexander, Bjørn God Kveld Norge 2012 Norway 24576 Alexander, Bjørn Adresseavisen 2008 Norway 24576 Alexander, Bjørn Her og Nå 2008 Norway 24576 Alexander, Bjørn Adresseavisen 2004 Norway 24576 Alexander, Bjørn Se og Hør 1998 Norway 28984 Allen, Corey The Independent: Viewspaper 2010 UK 28984 Allen, Corey Star Trek: The Next Generation 1994 USA 29026 Allen, Dave Uncut Magazine 2005 UK 29026 Allen, Dave The New York Times 2005 USA 29026 Allen, Dave The Scotsman 2005 UK 29026 Allen, Dave The Daily Telegraph 2005 UK 29026 Allen, Dave The Daily Telegraph 2005 UK 29026 Allen, Dave The Scotsman 2005 UK 29889 Allen, Patrick The Independent 2006 UK 29889 Allen, Patrick Daily Telegraph 2006 UK 33384 Altes, Steve The Washington Times 1998 USA 33799 Alton, John Ambito Financiero 1996 Argentina 33799 Alton, John La Nación 1996 Argentina 36790 Ambrosia, Gary Monterey Herald 2008 USA 37001 Amell, Stephen Entertainment Weekly 2012 USA 37515 Amico, Robert Variety 2000 USA 40237 Andersen, Hans Christian Bild & Bubbla 2005 Sweden 40237 Andersen, Hans Christian Letters Magazine 2005 Belgium 40237 Andersen, Hans Christian The Washington Post 2005 USA 40237 Andersen, Hans Christian Strip! 2005 Denmark 40237 Andersen, Hans Christian G2 (Guardian supplement) 2004 Guardian supplement 41462 Anderson, Gerry The Independent on Sunday 2007 UK 41462 Anderson, Gerry The Independent 2004 UK 41462 Anderson, Gerry Starlog 1987 USA 45910 Andrés López, Ángel de El Semanal TV 2004 Spain 49572 Antin, Jonathan Woman's World 2006 USA 49572 Antin, Jonathan Woman's World 2005 USA 52958 Arabia, Roman Daily Variety 2007 USA 54451 Arbouet, Michael J. Queens Ledger 2007 USA 54451 Arbouet, Michael J. New York Times 2006 USA 56663 Aria, Max Maria Hamilton's Best Kept Secrets 2012 USA 56663 Aria, Max The Examiner 2012 USA 56663 Aria, Max En las palabras de M.I.L.A 2012 USA 57353 Ariza, Liche Diario Libre 2009 Dominican Republic 58956 Armstrong, Vic Los Angeles Times 2003 USA 59427 Arnett, Will The Sydney Morning Herald 2007 Australia 59636 Arnold, Craig The Star 2013 Canada 59636 Arnold, Craig The Film Stage 2013 USA 59636 Arnold, Craig CBC News 2013 Canada 59636 Arnold, Craig Hollywood Life 2012 USA 67513 Atkins, Chet The Daily Telegraph 2001 UK 69159 Aude, Erik LA Times 2002 USA 70698 Austin, Ford The Daily Oklahoman 2007 USA 70698 Austin, Ford Reuters 2003 USA 70698 Austin, Ford Variety 1998 USA 74380 Azar, Pablo TV Notas 2011 USA 74380 Azar, Pablo TV y Novelas 2011 USA 74380 Azar, Pablo TeleNOVELA 2010 Spain 74380 Azar, Pablo TeleNOVELA 2006 Spain 74380 Azar, Pablo TV Notas 2005 USA 74380 Azar, Pablo Dos Mundos 2005 USA 79357 Bagby, Larry The Daily Universe of BYU 2001 U.S.A. 80510 Baier, Bret The Washington Post 2009 USA 80510 Baier, Bret

### La table Salary

In [0]:
%sql
create or replace temp view Salary as 
with R0 as (select id , name , element_at(split(value, '::'),1) as film_year,element_at(split(value, '::'),2) as montant from NameDetail where property="salary history" ) select id as id_person, name as name_person, regexp_extract(film_year,"([a-zA-Z0-9'?!.& ]+)",1) as film ,
cast(regexp_extract(film_year,'\\((.*?)\\)',1) as int) as year, cast(regexp_replace(regexp_extract(montant,"([0-9,]+)"),',','') as int) as amount,regexp_extract(montant,"([a-zA-Z$€£]+)") as currency
from R0;
 
select *from Salary

id_person name_person film year amount currency 1989 Abbott, Bud Rio Rita 1942 75000 $ 1989 Abbott, Bud One Night in the Tropics 1940 17500 $ 1989 Abbott, Bud The Abbott and Costello Show 1952 15000 $ 1989 Abbott, Bud In the Navy 1941 25000 $ 1989 Abbott, Bud Buck Privates 1941 25000 $ 1989 Abbott, Bud Hold That Ghost 1941 25000 $ 1989 Abbott, Bud Who Done It? 1942 25000 $ 1989 Abbott, Bud Jack and the Beanstalk 1952 250000 $ 1989 Abbott, Bud In Society 1944 40000 $ 1989 Abbott, Bud Abbott and Costello Meet the Invisible Man 1951 75000 $ 58984 Armus, Burton N.Y.P.D. 1967 100 $ 58984 Armus, Burton N.Y.P.D. 1967 2000 $ 86278 Bale, Christian The Dark Knight 2008 10000000 $ 86278 Bale, Christian Terminator Salvation 2009 8000000 $ 101482 Bartel, Paul Death Race 2000 1975 5500 $ 117565 Belafonte, Harry Carmen Jones 1954 1800 $ 121380 Belushi, John Animal House 1978 40000 $ 121380 Belushi, John Saturday Night Live 1975 750 $ 133590 Berry, Fred What's Happening Now! 1985 500 $ 141264 Biggs, Jason American Pie 1999 1000000 $ 141264 Biggs, Jason American Pie 2 2001 2000000 $ 141264 Biggs, Jason American Reunion 2012 5000000 $ 147616 Black, Jack Orange County 2002 2000000 $ 147616 Black, Jack Saving Silverman 2001 1000000 $ 147616 Black, Jack Shallow Hal 2001 2000000 $ 149989 Blake, Robert Baretta 1975 27500 $ 154649 Blue, Monte Intolerance 1916 5 $ 169391 Bosworth, Brian Stone Cold 1991 500000 $ 214216 Burton, Richard Anne of the Thousand Days 1969 1 $ 214216 Burton, Richard The V.I.P.s 1963 500000 $ 214216 Burton, Richard My Cousin Rachel 1952 50000 $ 214216 Burton, Richard The Night of the Iguana 1964 500000 $ 214216 Burton, Richard Look Back in Anger 1959 100000 $ 214216 Burton, Richard The Bramble Bush 1960 125000 $ 214216 Burton, Richard Ice Palace 1960 125000 $ 214216 Burton, Richard Cleopatra 1963 250000 $ 214216 Burton, Richard The Longest Day 1962 30000 $ 214216 Burton, Richard Spy Who Came In from the Cold 1965 750000 $ 214216 Burton, Richard Where Eagles Dare 1968 1000000 $ 214216 Burton, Richard Steiner 1978 750000 $ 214216 Burton, Richard Circle of Two 1981 750000 $ 214216 Burton, Richard Wagner 1983 1000000 $ 214216 Burton, Richard Lovespell 1979 750000 $ 214216 Burton, Richard Absolution 1978 125000 $ 214216 Burton, Richard The Medusa Touch 1978 500000 $ 214216 Burton, Richard Exorcist II 1977 1000000 $ 214216 Burton, Richard Brief Encounter 1974 600000 $ 214216 Burton, Richard The Comedians 1967 750000 $ 214216 Burton, Richard Who's Afraid of Virginia Woolf? 1966 750000 $ 214216 Burton, Richard Boom 1968 1000000 $ 214216 Burton, Richard Staircase 1969 1250000 $ 214216 Burton, Richard The Sandpiper 1965 500000 $ 214216 Burton, Richard Raid on Rommel 1971 1000000 $ 214216 Burton, Richard Wagner 1983 1000000 $ 214216 Burton, Richard Equus 1977 500000 $ 214216 Burton, Richard Alexander the Great 1956 100000 $ 223566 Cain, Dean Lois & Clark 1993 60000 $ 223566 Cain, Dean Lois & Clark 1993 75000 $ 223566 Cain, Dean Lois & Clark 1993 75000 $ 232478 Canet, Guillaume Last Night null 39000 EUR 232478 Canet, Guillaume Espion null 800000 EUR 232478 Canet, Guillaume L'affaire Farewell 2009 800000 EUR 232478 Canet, Guillaume Le dernier vol 2009 800000 EUR 232478 Canet, Guillaume La clef 2007 300000 EUR 232478 Canet, Guillaume La nouvelle guerre des boutons 2011 869000 EUR 232478 Canet, Guillaume Les petits mouchoirs 2010 1100000 EUR 234320 Canutt, Yakima The Devil Horse 1932 1000 $ 234320 Canutt, Yakima The Lightning Warrior 1931 125 $ 247173 Carvey, Dana Opportunity Knocks null 700000 $ 265065 Chaplin, Charles Making a Living 1914 150 $ 265065 Chaplin, Charles Kid Auto Races at Venice 1914 150 $ 265065 Chaplin, Charles Mabel's Strange Predicament 1914 150 $ 265065 Chaplin, Charles Caught in the Rain 1914 150 $ 265065 Chaplin, Charles Twenty Minutes of Love 1914 150 $ 265065 Chaplin, Charles The Tramp 1915 1250 $ 265065 Chaplin, Charles A Night Out null 1250 $ 267487 Chase, Chevy Saturday Night Live 1975 750 $ 267487 Chase, Chevy Chr

### La table Interview

In [0]:
%sql
create or replace temp view Interview as
select id as id_person,name as name_person,regexp_replace(regexp_extract(value,'("(.*?)" )',1),'"',"")as media,cast(regexp_extract(value,'([0-9][0-9][0-9][0-9])',1) as int) as year,regexp_extract(value,'\\((.*?)\\)',1) as country from NameDetail where property='interviews';
 
select * from Interview

id_person name_person media year country 9544 Adamíra, Jirí Kino 1985 Czechoslovakia 16503 Ainley, Anthony Starlog 1984 USA 16503 Ainley, Anthony Doctor Who Magazine 1982 UK 18099 Akin, Fatih Filmstart 2007 Germany 18099 Akin, Fatih Widescreen 2004 Germany 23191 Alderman, Ted Pearl Ledger 2004 USA 23233 Alderton, John Radio Times 1990 UK 24576 Alexander, Bjørn ABC7 News 2011 USA 24576 Alexander, Bjørn Rana Blad 2011 Norway 24576 Alexander, Bjørn Radio Adressa (Radio Station) 2010 Radio Station 24576 Alexander, Bjørn Adresseavisen 2008 Norway 24576 Alexander, Bjørn Radio Norge 2008 Norway 24962 Alexander, J. New York 2004 USA 26528 Alföldi, Róbert Elle 2002 Hungary 26528 Alföldi, Róbert Nõk Lapja 2001 Hungary 26528 Alföldi, Róbert Beau Monde 2001 Hungary 26528 Alföldi, Róbert Total Film 1999 Hungary 26528 Alföldi, Róbert Cosmopolitan 1999 Hungary 26528 Alföldi, Róbert Joy 1998 Hungary 28984 Allen, Corey Huffington Post 2010 USA 30759 Allio, René Positif 1968 France 40845 Anderson, Brett New Musical Express 2005 UK 40845 Anderson, Brett The Friday Review (Guardian supplement) 2005 Guardian supplement 40845 Anderson, Brett NME 1999 UK 40845 Anderson, Brett Melody Maker 1997 UK 40845 Anderson, Brett Melody Maker 1997 UK 41462 Anderson, Gerry The Independent 2007 UK 41462 Anderson, Gerry RRP 2005 UK 41462 Anderson, Gerry Dreamwatch 2004 UK 41462 Anderson, Gerry Dreamwatch 2004 UK 41462 Anderson, Gerry Dreamwatch 2003 UK 41462 Anderson, Gerry The Independent 2003 U.K. 41462 Anderson, Gerry Starlog 2003 USA 41462 Anderson, Gerry Starlog 1994 USA 41462 Anderson, Gerry Starlog 1987 USA 54905 Archer, Gem Q 2002 UK 54905 Archer, Gem Melody Maker 1997 UK 56361 Argenziano, Carmen TV Zone Special 2002 USA 56361 Argenziano, Carmen TV Zone Special 2000 USA 56361 Argenziano, Carmen Cult Times 2000 USA 56663 Aria, Max The Examiner 2012 USA 56663 Aria, Max Arrebatados 2012 USA 58265 Armitage, Richard Daily Mail 2006 UK 58265 Armitage, Richard Radio Times 2005 UK 58956 Armstrong, Vic Widescreen 2006 Germany 58984 Armus, Burton TV Zone Special 1998 UK 58984 Armus, Burton Starlog 1997 USA 59427 Arnett, Will Forbes 2011 USA 59427 Arnett, Will Maxim 2010 USA 59427 Arnett, Will Playboy 2007 USA 59427 Arnett, Will Premiere 2006 USA 67513 Atkins, Chet Guitar World 1996 USA 67513 Atkins, Chet Rolling Stone 1976 USA 74380 Azar, Pablo 15a20 2008 Mexico 74380 Azar, Pablo Carteles 2006 USA 77919 Bacon, Michael Post Magazine 2012 USA 77919 Bacon, Michael The Hollywood Reporter 2012 USA 85952 Baldwin, Adam Cult Times Special 2006 USA 86278 Bale, Christian Esquire 2010 USA 86278 Bale, Christian MovieScope Magazine 2008 UK 86278 Bale, Christian The Independent: Extra 2008 UK 86278 Bale, Christian Starlog 2008 USA 86278 Bale, Christian Parade 2008 USA 86278 Bale, Christian Widescreen 2005 Germany 86278 Bale, Christian The Independent Arts and Books Review 2005 UK 86278 Bale, Christian Toy Wishes 2005 USA 86278 Bale, Christian Stuff 2002 USA 86278 Bale, Christian Empire 2001 UK 86278 Bale, Christian Playboy 2001 USA 86278 Bale, Christian Fangoria 2000 USA 86278 Bale, Christian Hot Tickets Evening Standard 2000 UK 86278 Bale, Christian Interview 2000 US 86278 Bale, Christian Empire 1998 UK 86278 Bale, Christian Interview Magazine 1998 USA 86278 Bale, Christian Movieline 1997 USA 86278 Bale, Christian Detour Magazine 1996 USA 86278 Bale, Christian YM Magazine 1996 USA 86278 Bale, Christian Detour 1996 USA 86278 Bale, Christian Spin 1996 USA 86814 Ball, Alan TV Guide 2008 USA 86814 Ball, Alan The Advocate 2002 USA 86814 Ball, Alan The Advocate 2001 USA 95692 Barker, Ronnie Radio Times 1999 UK 95899 Barks, Carl Rackham 2001 Denmark 95899 Barks, Carl Hogan's Alley 2001 USA 95899 Barks, Carl BoDoï 2000 France 95899 Barks, Carl The Comics Journal 2000 USA 95899 Barks, Carl The Comics Journal 2000 USA 95899 Barks, Carl The Comics Journal 2000 USA 95899 Barks, Carl Stripschrift 2000 Holland 95899 Barks, Carl The Comics Journal 2000 USA 95899 Barks, Carl SWOF 1999 Switzerla

# Tâche 2
En se basant sur nos tables créees lors de la tache 1, nous allons crées des dimensions puis analyser les données selon ces dimensions.
Le fait que nous étudions est "le cast" (association entre une personne, une oeuvre et un rôle) qui est representé par une table contenant l'id de la personne, le salaire de la personne, l'id du role, le type du role et l'id du film. Ensuite nous allons l'analyser selon les dimensions suivantes:
- La dimension "Genre" contenant le genre de l'oeuvre.

- La dimension "Language" contenant la "langue" de l'oeuvre.

- La dimension "Release" contenant les "lieux" et les "dates de sortie" d'une oeuvre en hiérarchie jour,mois,année 

- La dimension "Nationnalité" contenant la "nationnalité".

- La dimension "DateNaissance" contenant la "date de naissance" en hiérarchie jour,mois,année

#### Les dimensions Genre Language Release ayant déja été créées, nous allons créer les deux dimensions qui restent

### La table Nationnalité

In [0]:
%sql
Create or replace temp view Nationnalite as
select id_person,birth_country as nationnalite from Person;
 
select * from Nationnalite

id_person nationnalite 1521 Italy 1668 Syria 1989 USA 3121 Japan 3482 Colombia 3892 null 4318 USSR 4523 USA 4662 USA 5803 Italy 6152 France 6466 Germany 6740 UK 6892 USA 7469 USA 7555 France 7915 Italy 8393 UK 8572 USA 8692 UK 9051 Canada 9199 null 9407 UK 9496 UK 9523 New Zealand 9544 Czechoslovakia 10263 Nigeria 10276 USA 10314 Netherlands 10895 USA 11139 Germany 11201 USA 11403 Romania 11694 Belgium 11784 null 11972 Netherlands 12053 France 12915 Spain 13218 USA 13897 Mexico 13977 Spain 14356 Spain 15021 UK 15032 Sweden 15706 Finland 15862 Sweden 16264 Japan 16503 UK 16879 Ireland 16897 UK 16926 Finland 17303 Japan 17579 Turkey 18099 West Germany 19728 Egypt 19856 USA 20322 UK 20554 Argentina 20644 USA 20889 Philippines 21113 Spain 21273 Mexico 21326 Germany 21653 Italy 21682 Portugal 21964 null 21992 UK 22060 UK 22788 UK 23191 USA 23233 UK 23240 UK 23353 USA 23424 USA 23526 Spain 23538 Switzerland 23613 Spain 23651 Portugal 24156 France 24576 Norway 24867 USA 25388 USA 25735 Spain 26355 Argentina 26528 null 27467 Yugoslavia 27771 null 28569 USA 28571 UK 28699 USA 28984 USA 29026 Ireland 29719 null 29889 Nyasaland [now Malawi] 29966 UK 30673 France 30759 France 31809 Cuba 31958 Sweden 32414 Spain 32627 Turkey 33085 USA 33120 USA 33375 USA 33384 USA 33799 Austria-Hungary (now Hungary) 34752 Spain 35197 Spain 35415 Japan 35967 null 36147 USA 36790 USA 36864 Hungary 36912 USA 37001 Canada 37515 USA 38999 UK 40237 Denmark 40845 UK 41420 Germany 41429 South Africa 41462 UK 42537 USA 42573 USA 42665 UK 42970 UK 43237 USA 43482 Spain 44869 Ireland 45241 USA 45475 Dordogne 45510 USA 45910 Spain 45943 Spain 46332 USA 46606 Italy 46630 UK 47406 USA 47413 Australia 47771 null 48002 USA 48572 USA 49024 USA 49332 USA 49572 USA 49895 USA 49974 Italy 50075 null 50161 USA 50223 USA 50630 Finland 51292 Japan 52466 USA 52893 France 52958 USA 53095 USA 53238 Japan 53477 null 53641 Belgium 53726 Spain 53763 Brazil 54348 France 54451 USA 54905 UK 54910 Australia 55259 now Austria 55664 Spain 56028 Germany 56361 USA 56535 Spain 56583 Greece 56970 Israel 57553 Turkey 57645 USA 57808 France 58037 Mexico 58265 UK 58787 USA 58956 UK 59427 Canada 59649 USA 60392 UK 60761 USA 60924 Spain 62008 UK 62118 USA 62645 France 62893 null 63793 USA 63825 USA 63838 UK 64121 UK 64134 Cuba 64241 UK 65465 Germany 65541 USA 66181 null 66292 USA 66663 Germany 66699 Turkey 66995 USA 67078 USA 67513 USA 67911 Canada 68531 UK 68754 Hong Kong 68962 France 69159 USA 69331 Germany 70039 Finland 70698 USA 71402 Brazil 71419 USA 72314 Soviet Union [now Russia] 72460 USA 74380 Mexico 74852 Mexico 74966 France [now Algeria] 75864 Yugoslavia 77475 Germany 77718 Germany 77761 UK 77908 USA 77919 USA 78120 Italy 78387 Italy 79313 Republic of Georgia] 79357 USA 79398 USA 79572 Italy 79578 USA 79746 USA 79753 USA 80118 Bulgaria 80558 British India 81131 UK 82547 Poland 82675 Suriname 83614 USA 83693 UK 83865 USA 84520 USA 85256 USSR 85952 USA 86087 USA 86278 UK 86345 Brazil 86438 Yugoslavia 86548 Brazil 86814 USA 87254 USA 87324 USA 88343 Portugal 88365 USA 88792 Romania 90381 UK 90431 USA 91116 UK 91125 UK 91217 Ireland 91571 Germany 92161 Spain 92678 USA 92809 Yugoslavia 93614 Brazil 94523 UK 95272 France 95692 UK 95872 Spain 95899 USA 97357 USA 97381 null 97928 Germany 98144 Brazil 98427 India 98544 Portugal 98895 Mexico 98911 Spain 98946 Spain 99516 USA 99671 USA 100257 UK 100296 null 100381 Chile 100492 Portugal 100524 Portugal 100707 USA 100712 Ireland 100918 Ireland 101122 UK 101238 Austria-Hungary (now Hungary) 101482 USA 101816 USA 102741 Rhodesia 102813 Czechoslovakia [now Czech Republic] 103045 Canada 103116 null 103399 Canada 103409 null 103579 USA 103794 USA 103842 USA 103912 USA 104056 USA 104211 Russia] 104472 Spain 106074 UK 106431 France 106839 UK 106949 Italy 107061 USA 108036 Germany 108528 Germany 108633 Venezuela 109376 USA 109417 Belgium 109529 Mexico 109939 USA 110648 USA 110777 Croatia 110878 USA 111161 USA 111818 USA 112216 USA 112322 USA 113033 Italy 11309

### La table Date de naissance

In [0]:
%sql
create or replace temp view DateDeNaissance as
select id_person,birth_year as year,birth_month as month,birth_day as day from Person
;
 
select * from DateDeNaissance

id_person year month day 1521 1955 May 20 1668 1906 November 15 1989 1895 October 2 3121 1917 March 28 3482 1968 February 28 3892 1958 October 24 4318 1980 February 20 4523 1916 March 26 4662 1958 February 28 5803 1957 null 6152 1899 July 5 6466 1945 March 14 6740 1890 June 5 6892 1987 November 4 7469 1884 February 11 7555 1908 April 4 7915 1957 July 30 8393 1928 December 20 8572 1963 February 7 8692 1931 February 14 9051 1946 September 20 9199 null July 11 9407 1974 null 9496 1930 February 16 9523 1890 January 4 9544 1926 April 2 10263 1968 May 9 10276 1952 February 28 10314 1977 December 23 10895 1929 February 4 11139 1965 November 10 11201 1953 September 15 11403 1983 August 31 11694 1941 October 24 11784 1917 null 11972 1933 December 11 12053 1944 February 13 12915 1949 null 13218 1982 January 15 13897 1918 January 29 13977 1899 null 14356 1948 October 10 15021 1990 September 12 15032 1984 December 3 15706 1970 December 1 15862 1943 June 10 16264 1961 November 30 16503 1932 August 20 16879 1942 August 30 16897 1867 April 16 16926 1936 July 11 17303 1939 May 8 17579 1977 December 1 18099 1973 August 25 19728 1921 December 26 19856 1981 February 16 20322 1930 September 18 20554 1946 September 9 20644 1952 April 17 20889 1978 September 4 21113 1973 November 5 21273 1982 August 12 21326 1891 September 22 21653 1882 November 30 21682 1948 August 2 21964 1968 February 12 21992 1957 July 14 22060 1953 February 19 22788 1931 null 23191 1970 September 22 23233 1940 November 27 23240 1970 October 31 23353 1943 June 11 23424 1972 May 30 23526 1973 June 28 23538 1971 June 1 23613 1962 null 23651 1881 March 10 24156 1877 September 9 24576 1989 April 12 24867 1970 April 15 25388 1902 November 19 25735 1917 November 11 26355 1961 null 26528 1967 November 22 27467 1934 October 15 27771 1951 null 28569 1941 April 13 28571 1965 June 19 28699 1866 April 8 28984 1934 June 29 29026 1936 July 6 29719 1920 April 16 29889 1927 March 17 29966 1940 March null 30673 1897 December 14 30759 1924 March 8 31809 1930 February 7 31958 1883 January 1 32414 1920 July 5 32627 1928 February 2 33085 1911 December 1 33120 1897 October 8 33375 1963 August 16 33384 1962 November 13 33799 1901 October 5 34752 1975 October 24 35197 1961 null 35415 1931 null 35967 1981 November 26 36147 1965 February 12 36790 1980 April 25 36864 1935 August 19 36912 1908 May 31 37001 1981 May 8 37515 1953 October 1 38999 1917 August 9 40237 1805 April 2 40845 1967 September 29 41420 1949 December 4 41429 1959 July 16 41462 1929 April 14 42537 1968 March 10 42573 1968 null 42665 1984 null 42970 1956 August 29 43237 1969 November 29 43482 1976 May 22 44869 1922 December 19 45241 1891 August 28 45475 1940 August 24 45510 1964 March 16 45910 1951 October 23 45943 1922 July 1 46332 1930 October 24 46606 1933 August 17 46630 1952 January 18 47406 1958 August 6 47413 1937 November 22 47771 1930 null 48002 1950 January 7 48572 1946 September 24 49024 1970 February 26 49332 1976 October 20 49572 1967 August 16 49895 1947 February 2 49974 1938 June 14 50075 1953 February 13 50161 1972 January 25 50223 1934 January 23 50630 1929 September 25 51292 1932 October 17 52466 1896 October 17 52893 1882 August 22 52958 1980 December 3 53095 1956 March 21 53238 1979 January 18 53477 1992 May null 53641 1987 null 53726 1964 January 11 53763 1987 April 9 54348 1907 April 9 54451 1971 April 15 54905 1965 December 7 54910 1973 March 24 55259 1899 July 24 55664 1976 null 56028 1932 June 13 56361 1943 October 27 56535 1948 September 6 56583 1918 null 56970 1975 August 17 57553 1937 September 7 57645 1907 May 12 57808 1950 August 6 58037 1912 May 9 58265 1971 August 22 58787 1973 August 28 58956 1946 October 5 59427 1970 May 4 59649 1925 January 23 60392 1971 null 60761 1935 December 14 60924 1940 null 62008 1971 June 1 62118 1980 July 1 62645 1873 April 29 62893 1947 October 31 63793 1978 May 27 63825 1884 August 28 63838 1977 January 13 64121 1976 December 16 64134 1964 June 6 64241 1941 October 16 65465 19

## Table de cast
Nous allons maintenant créer la table qui représente le fait "cast"

In [0]:
%sql
create or replace temp view Cast as
 
select  r.id as id_role,r.person_id as id_person,r.movie_id as id_movie, rt.role as type_role , s.amount as salaire, s.currency
from Title t,Cast_Info r left outer join Salary s on (s.id_person=r.person_id and t.title=s.film ),Role_Type rt
where  r.role_id=rt.id and t.id=r.movie_id
;
 
select * from Cast

id_role id_person id_movie type_role salaire currency 16255404 2202581 434 actress null null 19618701 2634949 434 actress null null 5806077 786248 434 actor null null 12920066 1770691 434 actress null null 21230535 2801406 1680 producer null null 18697034 2514889 2977 actress null null 31689471 3230279 2977 miscellaneous crew null null 26880882 44453 2977 cinematographer null null 12089685 1658620 2977 actor null null 21513831 2825107 3342 producer null null 31615473 3565387 3342 miscellaneous crew null null 21696608 2841048 3342 producer null null 32328582 3641142 3342 miscellaneous crew null null 1168964 162398 3345 actor null null 16287133 2207352 3981 actress null null 6102907 829555 3981 actor null null 7540975 1028514 3981 actor null null 25531013 3147896 3981 writer null null 25532641 3148050 3981 writer null null 22810336 1171861 5115 producer null null 23962973 3048050 5115 producer null null 3163136 423170 5115 actor null null 25986883 1171861 5115 writer null null 27640196 1511670 5115 cinematographer null null 14522243 1973199 5115 actress null null 5603185 754648 6416 actor null null 25315306 754648 6416 writer null null 11757412 1615043 7169 actor null null 31991937 159658 7430 miscellaneous crew null null 4036342 539437 7436 actor null null 20457790 2731741 8413 producer null null 2900412 385305 8413 actor null null 5042664 677150 8413 actor null null 21629354 2834711 8413 producer null null 25149087 2834711 8413 writer null null 8254352 1125307 8413 actor null null 8526257 1160508 8413 actor null null 29109845 308827 8413 director null null 30843356 3514400 8413 editor null null 31763881 70032 9005 miscellaneous crew null null 32339383 294876 9005 miscellaneous crew null null 20518862 179056 9005 producer null null 32507236 3658325 9005 miscellaneous crew null null 32634599 3670966 9005 miscellaneous crew null null 33056230 2817118 9005 miscellaneous crew null null 33666600 819572 9005 miscellaneous crew null null 21863046 751536 9005 producer null null 21942425 788897 9005 producer null null 34144964 1012873 9005 miscellaneous crew null null 24589034 294876 9005 writer null null 25312089 751536 9005 writer null null 11322836 1552439 9005 actor null null 32303531 281281 9376 miscellaneous crew null null 26141040 1279993 9376 writer null null 20686358 2751483 9597 producer null null 29710762 2893079 9597 director null null 30366278 3488856 9597 director null null 16644593 2254048 11564 actress null null 4433479 592424 11564 actor null null 21482074 592424 11564 producer null null 32624508 3670012 11564 miscellaneous crew null null 25059847 592424 11564 writer null null 33623569 3779843 11564 miscellaneous crew null null 26469852 3203314 11564 writer null null 26726326 3220219 11564 writer null null 8386557 1144040 12955 actor null null 31151705 1017540 13242 editor null null 34474083 2939136 13242 miscellaneous crew null null 34787510 2965505 13242 miscellaneous crew null null 35191544 2999990 13242 miscellaneous crew null null 35552632 3994935 13242 miscellaneous crew null null 23473682 3005746 13475 producer null null 23968554 3048580 13475 producer null null 9264236 1264577 14286 actor null null 18093607 2437464 15064 actress null null 6782000 928644 15064 actor null null 9748541 1328555 15064 actor null null 19026948 2559518 15765 actress null null 2471752 330271 15765 actor null null 11892373 1632066 15765 actor null null 23009556 2964371 16249 producer null null 5409327 725913 16249 actor null null 23886816 3043029 16249 producer null null 9784088 1333345 16249 actor null null 16320642 2211760 18330 actress null null 2813741 373653 18330 actor null null 31857505 3591299 19610 miscellaneous crew null null 31950718 1818794 19610 miscellaneous crew null null 31981812 2732960 19610 miscellaneous crew null null 34441810 2936376 19610 miscellaneous crew null null 27981700 3344261 19610 composer null null 15045864 2038699 19610 actress null null 1719960 233868 19980 actor null null 7521215 1025831 21133 actor nul

#### Selon la dimension Genre
Nombre de roles selon le genre du film

In [0]:
%sql
select g.genre, count(*) as nb_roles
from Cast c,Genre g
where c.id_movie=g.id_movie
group by Rollup(g.genre)
;

genre nb_roles War 3151 Film-Noir 100 Action 12287 Sport 2849 Western 2746 Adult 5984 Music 5577 History 4166 Reality-TV 1136 Romance 12872 Documentary 15036 Family 7429 Drama 50914 Adventure 7258 Comedy 37153 Sci-Fi 4793 Mystery 4911 Horror 6888 null 257536 Crime 10114 Musical 2757 Fantasy 5596 Short 31167 Biography 3897 Talk-Show 855 Thriller 12414 News 584 Game-Show 521 Animation 4381

#### selon la dimension language
Nombre de roles selon la langue du film

In [0]:
%sql
select l.language, count(*) as nb_roles
from Cast c,Langue l
where c.id_movie=l.id_movie
group by Rollup(l.language)
order by nb_roles DESC
;

language nb_roles null 241623 English 151356 Spanish 13372 German 12104 French 11218 Japanese 5813 Italian 5603 Portuguese 4933 Tagalog 2935 Filipino 2796 Russian 2650 Dutch 2357 Hindi 2189 Swedish 1821 Mandarin 1551 Danish 1406 Greek 1353 Finnish 1201 Cantonese 1171 Hungarian 1122 Polish 1099 Czech 1072 Turkish 969 Korean 804 Serbo-Croatian 798 Arabic 750 Catalan 616 Norwegian 549 Romanian 515 Hebrew 472 Telugu 358 Persian 351 None 350 Croatian 350 Latin 331 Serbian 307 Bengali 266 Thai 260 Slovenian 231 Malayalam 229 Estonian 216 Icelandic 193 Indonesian 188 Georgian 155 Malay 154 Tamil 150 Bulgarian 149 Lithuanian 136 Albanian 128 Urdu 126 Slovak 124 Oriya 110 Macedonian 107 Marathi 102 Mongolian 96 Galician 90 Azerbaijani 90 Welsh 84 Afrikaans 78 Bosnian 78 British Sign Language 77 Punjabi 75 Ukrainian 70 Yoruba 68 Chinese 59 Swiss German 58 Inuktitut 58 Armenian 54 Sinhala 46 Quechua 39 Maasai 39 Dari 36 Bambara 36 Letzebuergesh 35 Swahili 31 Amharic 30 Romansch 30 Scottish Gaelic 29 Dinka 28 Latvian 28 Hausa 26 Parsee 25 American Sign Language 24 Kinyarwanda 24 Azeri 23 Ju'hoan 23 Kannada 22 Gujarati 21 Basque 20 Tibetan 20 Yiddish 20 Irish Gaelic 19 Taiwanese 19 Uzbek 19 Purepecha 17 Bable 17 Turkmen 17 Indian Sign Language 14 East-Greenlandic 14 Jola-Fonyi 13 Sotho 13 Nepali 12 Kurdish 11 Maori 11 Vietnamese 10 Shona 9 Creole 9 Tarahumara 7 Haitian 7 Klingon 7 Hokkien 6 Burmese 5 Esperanto 4 Assamese 3 Wolof 2 Rajasthani 2

#### Dimension Release 
Nombre de roles en fonction de la date de sortie du film

In [0]:
%sql
select rel.year,rel.month,rel.day, count(*) as nb_roles
from Cast c,Release rel
where c.id_movie=rel.id_movie and rel.year is not null  and rel.month is not null and rel.day is not null
group by Rollup(rel.year,rel.month,rel.day)
order by year,month,day

year month day nb_roles null null null 733071 1899 null null 4 1899 December null 4 1899 December 13 4 1901 null null 3 1901 June null 1 1901 June 29 1 1901 November null 2 1901 November 13 2 1904 null null 1 1904 February null 1 1904 February 6 1 1905 null null 7 1905 December null 7 1905 December 23 7 1906 null null 1 1906 May null 1 1906 May 14 1 1907 null null 13 1907 December null 4 1907 December 14 4 1907 January null 2 1907 January 19 2 1907 May null 2 1907 May 20 2 1907 November null 4 1907 November 2 4 1907 September null 1 1907 September 14 1 1908 null null 11 1908 February null 2 1908 February 1 2 1908 January null 5 1908 January 19 5 1908 June null 2 1908 June 10 1 1908 June 28 1 1908 October null 1 1908 October 22 1 1908 September null 1 1908 September 19 1 1909 null null 74 1909 December null 4 1909 December 28 4 1909 February null 1 1909 February 8 1 1909 July null 31 1909 July 1 31 1909 June null 2 1909 June 25 1 1909 June 26 1 1909 March null 2 1909 March 26 1 1909 March 9 1 1909 May null 6 1909 May 22 6 1909 November null 2 1909 November 13 2 1909 October null 25 1909 October 1 10 1909 October 21 15 1909 September null 1 1909 September 24 1 1910 null null 68 1910 April null 15 1910 April 18 1 1910 April 19 1 1910 April 2 6 1910 April 28 4 1910 April 30 2 1910 April 6 1 1910 August null 3 1910 August 13 1 1910 August 23 1 1910 August 26 1 1910 December null 4 1910 December 23 4 1910 February null 1 1910 February 16 1 1910 January null 2 1910 January 14 2 1910 July null 7 1910 July 16 3 1910 July 2 1 1910 July 3 3 1910 June null 18 1910 June 10 1 1910 June 4 17 1910 March null 4 1910 March 28 4 1910 May null 10 1910 May 16 9 1910 May 26 1 1910 November null 1 1910 November 5 1 1910 September null 3 1910 September 26 3 1911 null null 218 1911 April null 32 1911 April 17 9 1911 April 21 6 1911 April 22 9 1911 April 25 2 1911 April 6 6 1911 August null 2 1911 August 12 2 1911 December null 16 1911 December 13 11 1911 December 30 3 1911 December 8 2 1911 February null 2 1911 February 25 2 1911 January null 1 1911 January 9 1 1911 July null 3 1911 July 3 1 1911 July 6 2 1911 June null 13 1911 June 1 2 1911 June 21 4 1911 June 8 7 1911 March null 1 1911 March 11 1 1911 May null 1 1911 May 24 1 1911 November null 31 1911 November 10 9 1911 November 14 1 1911 November 16 14 1911 November 24 1 1911 November 25 1 1911 November 29 1 1911 November 30 4 1911 October null 26 1911 October 1 8 1911 October 2 3 1911 October 21 4 1911 October 23 3 1911 October 26 4 1911 October 7 4 1911 September null 90 1911 September 15 1 1911 September 17 1 1911 September 25 30 1911 September 26 27 1911 September 28 23 1911 September 5 7 1911 September 9 1 1912 null null 177 1912 April null 5 1912 April 20 3 1912 April 7 2 1912 August null 12 1912 August 14 2 1912 August 19 6 1912 August 28 4 1912 December null 44 1912 December 16 5 1912 December 17 8 1912 December 20 3 1912 December 25 9 1912 December 27 5 1912 December 29 4 1912 December 31 10 1912 February null 6 1912 February 19 6 1912 January null 5 1912 January 13 2 1912 January 2 1 1912 January 9 2 1912 July null 7 1912 July 13 2 1912 July 4 5 1912 June null 6 1912 June 22 4 1912 June 28 2 1912 March null 11 1912 March 20 1 1912 March 30 10 1912 May null 24 1912 May 10 11 1912 May 14 7 1912 May 18 5 1912 May 22 1 1912 November null 12 1912 November 10 4 1912 November 14 4 1912 November 19 4 1912 October null 14 1912 October 12 6 1912 October 16 4 1912 October 4 3 1912 October 9 1 1912 September null 31 1912 September 11 7 1912 September 12 4 1912 September 16 9 1912 September 25 5 1912 September 28 3 1912 September 7 3 1913 null null 281 1913 April null 49 1913 April 10 7 1913 April 16 6 1913 April 17 8 1913 April 22 6 1913 April 28 4 1913 April 5 11 1913 April 6 5 1913 April 8 2 1913 August null 20 1913 August 6 17 1913 August 7 3 1913 December null 30 1913 December 1 12 1913 December 11 6 1913 December 16 7 1913 December 30 5 1913 February null 11 1913 February 10 5 1913 February 3 6

#### Dimension Nationnalité
Le cast selon la nationalité des personnes

In [0]:
%sql
select n.nationnality, count(*) as nb_roles
from Cast c,Nationnality n
where c.id_person=n.id_person
group by Rollup(n.nationnality)
order by nb_roles DESC
;

nationnality nb_roles null 159765 USA 58035 UK 16566 null 8690 Spain 7101 Germany 6982 Portugal 5039 Canada 4741 Japan 3916 France 3517 Brazil 3219 Australia 2620 Italy 2518 Netherlands 1817 Mexico 1627 Portugal 1615 Yugoslavia 1537 USA 1444 Sweden 1320 Finland 1306 Poland 1300 Hungary 1190 Argentina 1146 Belgium 891 Turkey 855 Austria 796 India 766 Denmark 701 Philippines 653 Ireland 580 Poland] 464 Denmark 457 China 455 Greece 423 Czechoslovakia [now Czech Republic] 418 Switzerland 395 Chile 385 Norway 322 Romania 303 Czechoslovakia 297 New Zealand 284 UK 272 Australia 267 Spain 265 France 236 Germany 230 Cuba 229 Puerto Rico 225 Norway 221 Israel 218 Canada 208 Czechoslovakia (now Czech Republic) 203 Croatia 201 South Africa 200 Hong Kong 191 West Germany 190 USSR [now Russia] 176 Egypt 164 Austria-Hungary [now Czech Republic] 164 Austria-Hungary [now Austria] 160 Ukraine] 157 Philippines 155 German Democratic Republic 153 Austria-Hungary (now Hungary) 150 Hungary 141 Russia] 134 Venezuela 134 Croatia/Hrvatska 134 Belgium 134 Russia 122 Bulgaria 119 USA. 117 Austria-Hungary (now Austria) 114 Israel 113 Colombia 113 Argentina 112 Yugoslavia [now Croatia] 108 Japan 108 New Zealand 100 Morocco 100 India 98 Austria-Hungary 97 Uruguay 92 Iran 92 Mozambique 90 Czech Republic 89 Russian Empire [now Russia] 88 Russia 87 Estonia 84 Mexico 81 South Korea 76 Czech Republic] 75 Dominican Republic 73 USSR 71 Finland 69 Angola 67 Sweden 65 Czech Republic 64 German Democratic Republic [now Federal Republic of Germany] 63 Austria-Hungary (now Czech Republic) 62 East Germany 61 Taiwan 60 Jamaica 58 Poland 58 Netherlands 57 USSR [now Ukraine] 56 France [now Algeria] 55 South Korea 54 Singapore 53 Indonesia 50 South Africa 50 Czechoslovakia [now Slovakia] 50 USSR (now Russia) 48 Italy 48 Bosnia and Herzegovina 48 Ecuador 44 Nigeria 44 Pakistan 43 Illinois USA 43 Peru 41 Taiwan 40 Ireland 40 Iceland 40 Serbia 39 China 39 Malaysia 38 Russia) 38 Latvia 37 Federal Republic of Germany] 35 Russian Empire [now Ukraine] 35 British India [now India] 34 Lebanon 33 Slovenia 33 Soviet Union [now Russia] 33 Czech Republic) 33 Panama 33 Czechoslovakia [now Slovak Republic] 33 British India 33 Hungary) 33 Zimbabwe 31 Czechoslovakia (now Slovakia) 31 Russian Empire 31 Korea 30 West Indies 30 Angola 30 Romania) 29 Austria 29 Mozambique 29 Algeria 28 Brazil 28 Croatia] 28 Yugoslavia (now Croatia) 28 now Austria 27 Romania 27 Turkey 26 Puerto Rico 26 Yugoslavia [now Serbia] 25 Lithuania] 25 Croatia) 23 Germany] 23 Cuba 23 Suriname 23 UK] 22 Czechoslovakia 22 USA] 22 Colombia 21 Protectorate Bohemia and Moravia [now Czech Republic] 21 Bulgaria 21 Albania 20 Egypt 20 Hong Kong 20 Yugoslavia (now Serbia) 20 Venezuela 19 Kenya 19 Slovakia 19 USSR 19 UK. 19 Vietnam 19 Palestine (now Israel) 19 Switzerland 17 Lithuania 17 France] 17 Romania] 16 British India [now Pakistan] 16 Iceland 16 Yugoslavia 16 Jamaica 15 Czechoslovakia. [now in Czech Republic] 15 Ukraine 15 Austria-Hungary [now Hungary] 15 West Germany [now in Germany] 15 India) 14 Netherlands Antilles 14 England 14 Bahrain 14 Malaysia 14 USSR [now Republic of Georgia] 14 Tunisia 14 Thailand 13 Palestine [now Israel] 13 Greece 13 Northern Ireland 13 Macedonia 13 Chile 13 Haiti 13 Belarus] 13 Soviet Union 13 Croatia 13 Buenos Aires 12 Hawaii 12 Honduras 12 Kazakhstan] 11 Austria-Hungary. [now in Czech Republic] 11 Iran 11 Austria-Hungary 11 Bahamas 11 Yugoslavia [now Montenegro] 11 USSR [now Azerbaijan] 11 Portugal (now Angola) 11 Cyprus 11 UK) 11 England 11 Bangladesh 11 Georgia 11 British India (now Pakistan) 11 French Protectorate of Morocco [now Morocco] 10 Austria-Hungary [now Croatia] 10 Czechoslovakia [now Czech Republic] 10 Czechoslovakia. [now Czech Republic] 10 British India (now India) 10 Ukraine 10 Senegal 10 USSR [now Belarus] 10 Burma 9 French Protectorate Tunisia [now Tunisia] 9 Slovakia) 9 U.S. Virgin Islands 9 Bosnia and Herzegovina) 9 Czech republic) 9 Kenya 9 Soviet Union [now Latvia] 9 Repub

#### Selon la dimension DateDeNaissance
Nombre de roles selon la date de naissance des personnes

In [0]:
%sql
select dn.year,dn.month,dn.day, count(*) as nb_roles
from Cast c,DateDeNaissance dn
where c.id_person=dn.id_person and dn.year is not null  and dn.month is not null and dn.day is not null
group by Rollup(dn.year,dn.month,dn.day)
order by year,month,day

year month day nb_roles null null null 145082 1469 null null 1 1469 May null 1 1469 May 3 1 1547 null null 2 1547 September null 2 1547 September 29 2 1564 null null 12 1564 April null 11 1564 April 23 11 1564 February null 1 1564 February 23 1 1606 null null 1 1606 June null 1 1606 June 6 1 1622 null null 4 1622 c null 4 1622 c 15 4 1628 null null 2 1628 November null 2 1628 November 28 2 1639 null null 1 1639 December null 1 1639 December 22 1 1660 null null 1 1660 September null 1 1660 September 13 1 1684 null null 1 1684 December null 1 1684 December 3 1 1730 null null 1 1730 November null 1 1730 November 10 1 1732 null null 1 1732 April null 1 1732 April 1 1 1748 null null 1 1748 December null 1 1748 December 10 1 1749 null null 1 1749 August null 1 1749 August 28 1 1757 null null 2 1757 November null 2 1757 November 28 2 1770 null null 1 1770 December null 1 1770 December 16 1 1771 null null 2 1771 August null 2 1771 August 15 2 1775 null null 1 1775 July null 1 1775 July 9 1 1777 null null 2 1777 October null 2 1777 October 18 2 1779 null null 1 1779 July null 1 1779 July 15 1 1785 null null 2 1785 January null 2 1785 January 4 2 1786 null null 2 1786 February null 2 1786 February 24 2 1789 null null 3 1789 September null 3 1789 September 15 3 1793 null null 1 1793 June null 1 1793 June 20 1 1797 null null 1 1797 August null 1 1797 August 30 1 1799 null null 7 1799 August null 1 1799 August 1 1 1799 June null 2 1799 June 6 2 1799 May null 4 1799 May 20 4 1802 null null 6 1802 February null 2 1802 February 26 2 1802 July null 4 1802 July 24 4 1803 null null 1 1803 September null 1 1803 September 28 1 1804 null null 1 1804 January null 1 1804 January 26 1 1805 null null 5 1805 April null 5 1805 April 2 5 1807 null null 2 1807 December null 1 1807 December 17 1 1807 February null 1 1807 February 27 1 1808 null null 2 1808 June null 1 1808 June 19 1 1808 November null 1 1808 November 2 1 1809 null null 3 1809 January null 2 1809 January 19 2 1809 March null 1 1809 March 31 1 1810 null null 4 1810 March null 2 1810 March 1 1 1810 March 2 1 1810 May null 1 1810 May 18 1 1810 September null 1 1810 September 29 1 1811 null null 1 1811 June null 1 1811 June 17 1 1812 null null 10 1812 February null 9 1812 February 7 9 1812 May null 1 1812 May 12 1 1814 null null 1 1814 June null 1 1814 June 8 1 1815 null null 2 1815 April null 1 1815 April 24 1 1815 May null 1 1815 May 6 1 1816 null null 1 1816 April null 1 1816 April 21 1 1817 null null 1 1817 September null 1 1817 September 5 1 1818 null null 2 1818 July null 1 1818 July 30 1 1818 November null 1 1818 November 9 1 1819 null null 3 1819 December null 2 1819 December 30 2 1819 May null 1 1819 May 24 1 1820 null null 1 1820 March null 1 1820 March 20 1 1821 null null 5 1821 August null 1 1821 August 11 1 1821 October null 3 1821 October 30 3 1821 September null 1 1821 September 24 1 1824 null null 4 1824 January null 3 1824 January 8 3 1824 July null 1 1824 July 27 1 1827 null null 1 1827 June null 1 1827 June 12 1 1828 null null 3 1828 August null 1 1828 August 28 1 1828 February null 1 1828 February 8 1 1828 March null 1 1828 March 20 1 1831 null null 3 1831 February null 2 1831 February 21 2 1831 September null 1 1831 September 5 1 1832 null null 1 1832 April null 1 1832 April 19 1 1834 null null 2 1834 January null 2 1834 January 1 2 1835 null null 6 1835 January null 1 1835 January 25 1 1835 June null 1 1835 June 2 1 1835 November null 3 1835 November 30 3 1835 October null 1 1835 October 4 1 1836 null null 3 1836 February null 1 1836 February 17 1 1836 November null 2 1836 November 18 2 1837 null null 2 1837 December null 2 1837 December 26 2 1839 null null 5 1839 August null 2 1839 August 8 2 1839 January null 1 1839 January 1 1 1839 June null 1 1839 June 21 1 1839 March null 1 1839 March 21 1 1840 null null 2 1840 May null 1 1840 May 7 1 1840 September null 1 1840 September 2 1 1841 null null 3 1841 August null 2 1841 August 18 2 1841 July null 1 1841 July 3 1 1842 null n

# Tâche 3
Nous allons enrichir nos informations avec des données provenant de MovieLens Database. Les propriétés ajoutées sont : 
- la note de chaque film 
- le nombre de votes
- la popularité du film

### La table films

In [0]:
schema_title = """
    index INT,
    id INT,
    popularity FLOAT,
    title STRING,
    note FLOAT,
    nb_votes INT      
        """
 
films = spark.read.csv(path ="/FileStore/tables/films.csv", schema = schema_title).persist()
films.createOrReplaceTempView("Films")
 
display(films)

index id popularity title note nb_votes null null null title null null 0 862 22.773 Toy Story 7.9 9550 1 8844 2.947 Jumanji 7.1 5594 2 15602 6.076 Grumpier Old Men 6.5 140 4 11862 6.817 Father of the Bride Part II 6.1 288 5 949 13.666 Heat 7.8 3002 6 11860 6.177 Sabrina 6.1 260 8 9091 5.89 Sudden Death 5.7 279 9 710 16.629 GoldenEye 6.8 1853 10 9087 6.165 The American President 6.6 299 11 12110 8.435 Dracula: Dead and Loving It 5.8 366 12 21032 8.735 Balto 7.2 947 13 10858 5.835 Nixon 7.0 123 14 1408 7.02 Cutthroat Island 5.8 221 15 524 12.757 Casino 7.9 2283 16 4584 8.861 Sense and Sensibility 7.4 647 17 5 8.995 Four Rooms 6.3 1089 18 9273 8.87 Ace Ventura: When Nature Calls 6.2 2019 19 11517 7.826 Money Train 5.6 335 20 8012 10.099 Get Shorty 6.5 451 21 1710 5.32 Copycat 6.5 382 22 9691 8.278 Assassins 6.2 624 23 12665 7.691 Powder 6.4 218 24 451 11.543 Leaving Las Vegas 7.2 567 25 16420 3.732 Othello 6.6 60 26 9263 7.539 Now and Then 6.8 152 27 17015 3.941 Persuasion 7.6 52 28 902 9.141 The City of Lost Children 7.5 465 30 9909 6.308 Dangerous Minds 6.5 402 31 63 14.048 Twelve Monkeys 7.5 4106 33 9598 10.096 Babe 6.1 1425 35 687 7.113 Dead Man Walking 7.4 595 38 9603 10.455 Clueless 7.1 1691 41 11443 5.585 Dead Presidents 6.6 113 43 9312 10.225 Mortal Kombat 5.6 835 44 577 6.814 To Die For 6.7 303 45 11861 6.04 How to Make an American Quilt 6.3 70 46 807 23.323 Se7en 8.3 9940 47 10530 11.145 Pocahontas 6.9 2932 48 8391 3.0 When Night Is Falling 6.6 28 49 629 14.51 The Usual Suspects 8.2 5341 51 11448 5.752 Mighty Aphrodite 6.7 245 53 26441 3.866 The Big Green 5.1 67 56 9089 4.715 Home for the Holidays 6.3 68 57 11010 7.443 The Postman 7.9 417 59 11359 5.893 The Indian in the Cupboard 6.0 246 60 17182 5.058 Eye for an Eye 6.0 107 61 2054 5.998 Mr. Holland's Opus 7.1 165 62 10607 8.749 Don't Be a Menace to South Central While Drinking Your Juice in the Hood 6.2 329 63 19760 2.177 Two If by Sea 4.8 28 64 9536 7.166 Bio-Dome 4.4 169 65 11525 4.029 Lawnmower Man 2: Beyond Cyberspace 2.9 57 67 4482 5.332 French Twist 6.2 116 68 10634 8.616 Friday 7.1 783 69 755 13.908 From Dusk Till Dawn 6.9 2810 70 11859 6.247 Fair Game 4.1 94 73 20927 3.725 Bed of Roses 5.3 42 75 9102 7.377 Screamers 6.2 224 78 9623 6.175 The Juror 5.5 141 80 400 7.27 Things to Do in Denver When You're Dead 6.6 148 81 880 3.016 Antonia's Line 7.4 48 84 8447 1.909 Angels and Insects 6.5 22 85 10534 6.647 White Squall 6.3 142 86 17414 5.644 Dunston Checks In 5.1 96 87 13997 6.482 Black Sheep 6.0 158 88 2086 6.264 Nick of Time 6.1 304 90 9095 6.449 Mary Reilly 5.8 124 91 12158 5.413 Vampire in Brooklyn 4.7 204 92 9283 5.721 Beautiful Girls 6.8 172 93 9208 9.785 Broken Arrow 5.9 671 95 406 7.631 La Haine 8.0 1332 98 11062 6.438 City Hall 6.1 105 99 13685 7.843 Bottle Rocket 6.8 437 101 2045 3.258 Unforgettable 5.6 40 102 9614 13.288 Happy Gilmore 6.5 1229 103 688 9.167 The Bridges of Madison County 7.5 739 104 11907 0.6 Nobody Loves Me 4.9 7 105 10874 5.451 Muppet Treasure Island 6.4 153 108 197 17.3 Braveheart 7.9 5217 109 103 15.527 Taxi Driver 8.1 4815 115 16934 1.599 The Young Poisoner's Handbook 7.1 27 116 10324 1.861 If Lucy Fell 4.8 21 120 11066 6.87 Boomerang 5.5 232 121 11104 6.95 Chungking Express 8.0 441 123 2074 6.046 Flirting with Disaster 6.2 99 130 11863 6.053 Jade 5.2 79 133 9101 6.249 Down Periscope 5.8 147 135 5757 0.6 Man of the Year 3.8 2 138 9302 5.092 Up Close & Personal 6.2 91 139 11000 7.715 The Birdcage 7.0 500 142 16388 2.446 The Brothers McMullen 6.0 37 143 9737 10.498 Bad Boys 6.6 2761 145 10474 7.629 The Basketball Diaries 7.3 795 146 22279 2.395 An Awfully Big Adventure 6.5 16 148 568 25.637 Apollo 13 7.4 2655 149 11780 7.825 Rob Roy 6.7 257 151 414 10.796 Batman Forever 5.3 2597 152 649 8.597 Belle de Jour 7.5 289 153 1873 1.715 Beyond Rangoon 6.8 30 154 5894 3.674 Blue in the Face 6.9 53 155 1775 5.809 Canadian Bacon 5.9 90 156 8839 11.041 Casper 6.2 2182 157 20649 6.056 Clockers 6.9 112 158 10329 8.594 Congo 5.2 353 159 8963 10.57 C

#### Ajout d'une nouvelle dimensions :
- NoteMovies

Ensuite nous étudierons le fait "cast" selon cette nouvelle dimension

In [0]:
%sql
create or replace temp view NoteMovies as 
select distinct td.id, td.title,f.popularity, round(f.note,0) as note, f.nb_votes
from TitleDetail td, Films f
where td.title=f.title
;
 
select * from NoteMovies

id title popularity note nb_votes 132129 The Hit 4.759 7.0 59 205126 Contact 11.586 7.0 2081 291541 Dead or Alive 2.889 7.0 58 358988 The Bank Job 8.02 7.0 1036 412272 El Dorado 5.67 7.0 163 441977 Staying Alive 8.219 5.0 179 469182 Beauty and the Beast 5.484 8.0 243 1146626 Jeepers Creepers 2 7.33 6.0 621 1197722 Missing in Action 6.108 6.0 173 1283883 The Big One 2.763 7.0 38 1362336 The Killer 5.918 8.0 285 1723692 Betsy's Wedding 2.47 6.0 13 1745294 Breathing Room 3.085 4.0 38 1842848 Double Trouble 7.132 7.0 221 1844344 Dracula 6.564 7.0 188 1844344 Dracula 7.139 7.0 447 1844344 Dracula 10.656 7.0 2106 1869412 Enigma 1.296 7.0 10 1888361 Fever Pitch 6.022 6.0 301 1888361 Fever Pitch 4.855 7.0 87 1926073 Grace Is Gone 6.776 6.0 56 2343570 The Adventures of Mark Twain 2.168 7.0 32 2355179 The Cave 6.755 5.0 354 2384793 The Last of the Mohicans 8.628 7.0 1287 2395361 The Motel 0.6 7.0 3 2407130 The Reluctant Dragon 4.582 7.0 46 147988 A Christmas Carol 14.244 7.0 2278 382237 Halloween 13.134 8.0 2215 392477 Die Hard 23.545 8.0 5903 652268 The Party 6.145 7.0 282 652268 The Party 7.775 7.0 513 735839 Paparazzi 8.655 6.0 89 851986 Great Expectations 6.226 7.0 113 867429 Machete 8.518 6.0 1759 890239 Red 3.596 7.0 72 914890 All or Nothing 3.238 7.0 53 1101298 Fool's Gold 7.115 6.0 711 1271795 The Adventures of Robin Hood 7.497 8.0 275 1276841 Paintball 3.06 4.0 59 1325502 Rebecca 9.059 8.0 599 1889014 Fifty Pills 2.507 5.0 25 1911420 Garden State 7.936 7.0 952 920274 No Retreat, No Surrender 7.183 6.0 153 931298 Great Expectations 6.178 7.0 228 1356920 Decoy 1.266 6.0 11 1401982 Class 4.53 6.0 62 1593643 Stardust 8.529 7.0 2061 1645834 A Christmas Carol 3.358 7.0 51 1654259 A Nightmare on Elm Street: The Dream Child 9.311 5.0 476 1688265 Angelus 0.6 8.0 4 1694638 Aria 1.557 6.0 14 1767455 Chaos Theory 6.992 6.0 193 1955884 Homecoming 4.352 5.0 74 2005888 Julia 3.231 7.0 37 2182616 Our Man in Havana 3.327 7.0 37 2352202 The Boys 0.867 7.0 5 2388912 The Love Bug 8.096 6.0 223 2418323 The Taking of Pelham 1 2 3 9.958 6.0 1547 237930 Sleeping with the Enemy 8.564 6.0 412 372935 Offside 2.357 7.0 50 513357 Do Not Disturb 2.115 5.0 17 568354 Crash 5.737 7.0 366 720815 The Importance of Being Earnest 1.948 8.0 37 851986 Great Expectations 6.178 7.0 228 903871 Teacher's Pet 1.17 6.0 9 919362 Down in the Valley 6.17 6.0 101 1278537 Inferno 5.744 7.0 205 1330649 Deception 7.736 6.0 323 1330649 Deception 2.369 7.0 18 1369028 Dazed and Confused 7.812 8.0 915 1727388 Big Game 1.031 4.0 2 186463 High Anxiety 6.02 7.0 133 348012 When the Wind Blows 4.37 7.0 96 403064 Weird Science 8.926 6.0 591 542991 The Ghost Writer 7.645 7.0 1082 1005692 The Italian Job 7.102 7.0 294 1052948 Fire and Ice 4.51 6.0 63 1243384 Alien 22.446 8.0 7144 1257207 1984 2.85 7.0 35 1287524 To Catch a Thief 6.842 7.0 538 1349872 Zero Tolerance 1.719 7.0 23 1591041 Wanted 2.51 6.0 48 1645834 A Christmas Carol 5.147 7.0 71 1664195 Ace in the Hole 6.714 8.0 217 1714929 Basic Instinct 14.358 7.0 1463 1763216 Catch-22 5.923 7.0 107 2126940 Monkey Business 4.476 7.0 52 2294518 Slumdog Millionaire 13.059 8.0 5405 59231 Where the Heart Is 6.9 7.0 318 62618 Gaslight 6.809 7.0 127 147988 A Christmas Carol 5.147 7.0 71 548400 The Great Gatsby 6.39 6.0 216 1306623 Manhunt 4.079 5.0 39 1762827 Casualties of War 7.011 7.0 312 1880342 Face 1.767 6.0 26 212346 Hide and Seek 10.683 6.0 755 309354 Female Trouble 3.727 7.0 58 384026 The Visitor 6.029 7.0 196 469182 Beauty and the Beast 20.017 8.0 5360 606074 The Visitors 7.832 7.0 877 823161 Taxi 9.136 7.0 1124 862744 Homecoming 4.352 5.0 74 931298 Great Expectations 6.226 7.0 113 1075765 The Arrival 14.984 6.0 297 1221384 The Chosen 1.4 7.0 7 1483708 Blind Man's Bluff 3.031 7.0 37 1645834 A Christmas Carol 14.244 7.0 2278 1776735 Circle of Iron 3.427 6.0 22 1852129 Easy Money 4.4 6.0 48 1878534 Expired 1.929 6.0 15 1916458 Ghost Dog: The Way of the Samurai 7.45 7.0 508 1937601 Harakiri 8.522 8.0 227 2137707 My Darling Clementine 6.955 8

### Selon la dimension NoteMovies
Nombre de roles selon le genre de films et des notes

In [0]:
%sql
select g.genre,nm.note, count(*) as nb_roles
from Cast c,Genre g, NoteMovies nm
where c.id_movie=g.id_movie and nm.id=c.id_movie
group by cube(g.genre,nm.note)
order by genre,note
;

genre note nb_roles null null 27881 null 2.0 8 null 3.0 19 null 4.0 1096 null 5.0 3832 null 6.0 11250 null 7.0 9551 null 8.0 2125 Action null 1616 Action 4.0 8 Action 5.0 402 Action 6.0 784 Action 7.0 281 Action 8.0 141 Adult null 113 Adult 5.0 15 Adult 6.0 33 Adult 7.0 50 Adult 8.0 15 Adventure null 952 Adventure 4.0 36 Adventure 5.0 217 Adventure 6.0 316 Adventure 7.0 294 Adventure 8.0 89 Animation null 427 Animation 4.0 8 Animation 5.0 69 Animation 6.0 92 Animation 7.0 237 Animation 8.0 21 Biography null 582 Biography 6.0 350 Biography 7.0 161 Biography 8.0 71 Comedy null 3636 Comedy 4.0 343 Comedy 5.0 1031 Comedy 6.0 1313 Comedy 7.0 949 Crime null 1522 Crime 4.0 91 Crime 5.0 146 Crime 6.0 599 Crime 7.0 686 Documentary null 542 Documentary 5.0 13 Documentary 6.0 10 Documentary 7.0 395 Documentary 8.0 124 Drama null 6048 Drama 2.0 4 Drama 3.0 19 Drama 4.0 309 Drama 5.0 503 Drama 6.0 2032 Drama 7.0 2527 Drama 8.0 654 Family null 720 Family 4.0 8 Family 5.0 151 Family 6.0 396 Family 7.0 154 Family 8.0 11 Fantasy null 1181 Fantasy 5.0 220 Fantasy 6.0 721 Fantasy 7.0 240 Film-Noir null 53 Film-Noir 6.0 53 History null 389 History 5.0 8 History 6.0 171 History 7.0 49 History 8.0 161 Horror null 1345 Horror 4.0 88 Horror 5.0 221 Horror 6.0 489 Horror 7.0 512 Horror 8.0 35 Music null 448 Music 6.0 242 Music 7.0 180 Music 8.0 26 Musical null 121 Musical 6.0 115 Musical 8.0 6 Mystery null 795 Mystery 4.0 8 Mystery 5.0 58 Mystery 6.0 439 Mystery 7.0 290 News null 13 News 5.0 13 Reality-TV null 10 Reality-TV 5.0 6 Reality-TV 6.0 4 Romance null 1962 Romance 4.0 153 Romance 5.0 83 Romance 6.0 1098 Romance 7.0 391 Romance 8.0 237 Sci-Fi null 615 Sci-Fi 4.0 36 Sci-Fi 5.0 106 Sci-Fi 6.0 265 Sci-Fi 7.0 208 Short null 928 Short 2.0 4 Short 4.0 8 Short 5.0 104 Short 6.0 323 Short 7.0 445 Short 8.0 44 Sport null 759 Sport 5.0 227 Sport 6.0 105 Sport 7.0 391 Sport 8.0 36 Talk-Show null 16 Talk-Show 7.0 16 Thriller null 2701 Thriller 5.0 218 Thriller 6.0 1267 Thriller 7.0 973 Thriller 8.0 243 War null 297 War 5.0 13 War 6.0 11 War 7.0 114 War 8.0 159 Western null 90 Western 5.0 8 Western 6.0 22 Western 7.0 8 Western 8.0 52

In [0]:
# Tache 4